In [1]:
from sklearnex import patch_sklearn 

import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import zipfile
from pandas import concat

from sklearn.preprocessing import MinMaxScaler, StandardScaler, RobustScaler, QuantileTransformer, MaxAbsScaler, Normalizer, PowerTransformer, minmax_scale
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, roc_curve, confusion_matrix, classification_report, fbeta_score, accuracy_score
from sklearn.ensemble import RandomForestClassifier, VotingClassifier, HistGradientBoostingClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.semi_supervised import SelfTrainingClassifier

from lightgbm import LGBMClassifier
from xgboost import XGBClassifier
from catboost import CatBoostClassifier

In [2]:
house1_power_blk2 = pd.read_csv('data/house1_power_blk2_labels.zip',compression='zip')
house1_power_blk2['datetime'] = pd.to_datetime(house1_power_blk2['datetime'])
house1_power_blk2 = house1_power_blk2.set_index('datetime')

In [3]:
house1_power_blk2

mains  activity
datetime                            
2016-03-06 00:00:00  473.0         0
2016-03-06 00:00:01  474.0         0
2016-03-06 00:00:02  476.0         0
2016-03-06 00:00:03  476.0         0
2016-03-06 00:00:04  475.0         0
...                    ...       ...
2016-05-07 22:59:55  604.0         0
2016-05-07 22:59:56  602.0         0
2016-05-07 22:59:57  602.0         0
2016-05-07 22:59:58  600.0         0
2016-05-07 22:59:59  603.0         0

[5439600 rows x 2 columns]

In [2]:
house1_power_blk2 = pd.read_csv('data/house1_power_blk2_labels.zip',compression='zip')
house1_power_blk2['datetime'] = pd.to_datetime(house1_power_blk2['datetime'])
house1_power_blk2 = house1_power_blk2.set_index('datetime')

nos_donnees = house1_power_blk2.copy()
data = nos_donnees[['mains']]
load_val = data[['mains']]
window = data.expanding()
new_dataframe = concat([window.min(),  window.mean(), window.max(), load_val.shift(-1)], axis=1)
new_dataframe.columns = ['min', 'mean', 'max', 'load+1']
new_dataframe['hour'] = [new_dataframe.index[i].hour for i in range(len(new_dataframe))]
new_dataframe['month'] = [new_dataframe.index[i].month for i in range(len(new_dataframe))]
new_dataframe['dayofweek'] = [new_dataframe.index[i].day for i in range(len(new_dataframe))]
new_dataframe['mains'] = nos_donnees['mains']
new_dataframe['activity'] = nos_donnees['activity']
house1_power_blk2 = new_dataframe.dropna()

house1_power_blk2

min         mean      max  load+1  hour  month  \
datetime                                                                
2016-03-06 00:00:00  473.0   473.000000    473.0   474.0     0      3   
2016-03-06 00:00:01  473.0   473.500000    474.0   476.0     0      3   
2016-03-06 00:00:02  473.0   474.333333    476.0   476.0     0      3   
2016-03-06 00:00:03  473.0   474.750000    476.0   475.0     0      3   
2016-03-06 00:00:04  473.0   474.800000    476.0   476.0     0      3   
...                    ...          ...      ...     ...   ...    ...   
2016-05-07 22:59:54  225.0  1104.073761  17206.0   604.0    22      5   
2016-05-07 22:59:55  225.0  1104.073669  17206.0   602.0    22      5   
2016-05-07 22:59:56  225.0  1104.073577  17206.0   602.0    22      5   
2016-05-07 22:59:57  225.0  1104.073485  17206.0   600.0    22      5   
2016-05-07 22:59:58  225.0  1104.073392  17206.0   603.0    22      5   

                     dayofweek  mains  activity  
datetime                                         
2016-03-06 00:00:00          6  473.0         0  
2016-03-06 00:00:01          6  474.0         0  
2016-03-06 00:00:02          6  476.0         0  
2016-03-06 00:00:03          6  476.0         0  
2016-03-06 00:00:04          6  475.0         0  
...                        ...    ...       ...  
2016-05-07 22:59:54          7  601.0         0  
2016-05-07 22:59:55          7  604.0         0  
2016-05-07 22:59:56          7  602.0         0  
2016-05-07 22:59:57          7  602.0         0  
2016-05-07 22:59:58          7  600.0         0  

[5439569 rows x 9 columns]

In [3]:
house2_power_blk1 = pd.read_csv('data/house2_power_blk1_labels.zip',compression='zip')
house2_power_blk1['datetime'] = pd.to_datetime(house2_power_blk1['datetime'])
house2_power_blk1 = house2_power_blk1.set_index('datetime')

nos_donnees = house2_power_blk1.copy()
data = nos_donnees[['mains']]
load_val = data[['mains']]
window = data.expanding()
new_dataframe = concat([window.min(),  window.mean(), window.max(), load_val.shift(-1)], axis=1)
new_dataframe.columns = ['min', 'mean', 'max', 'load+1']
new_dataframe['hour'] = [new_dataframe.index[i].hour for i in range(len(new_dataframe))]
new_dataframe['month'] = [new_dataframe.index[i].month for i in range(len(new_dataframe))]
new_dataframe['dayofweek'] = [new_dataframe.index[i].day for i in range(len(new_dataframe))]
new_dataframe['mains'] = nos_donnees['mains']
new_dataframe['activity'] = nos_donnees['activity']
house2_power_blk1 = new_dataframe.dropna()

house2_power_blk1

min        mean     max  load+1  hour  month  \
datetime                                                              
2017-09-12 23:00:00  103.0  103.000000   103.0   101.0    23      9   
2017-09-12 23:00:01  101.0  102.000000   103.0   104.0    23      9   
2017-09-12 23:00:02  101.0  102.666667   104.0   104.0    23      9   
2017-09-12 23:00:03  101.0  103.000000   104.0   105.0    23      9   
2017-09-12 23:00:04  101.0  103.400000   105.0   107.0    23      9   
...                    ...         ...     ...     ...   ...    ...   
2017-11-10 23:59:54    1.0  343.545136  7753.0   210.0    23     11   
2017-11-10 23:59:55    1.0  343.545110  7753.0   219.0    23     11   
2017-11-10 23:59:56    1.0  343.545086  7753.0   216.0    23     11   
2017-11-10 23:59:57    1.0  343.545061  7753.0   215.0    23     11   
2017-11-10 23:59:58    1.0  343.545036  7753.0   209.0    23     11   

                     dayofweek  mains  activity  
datetime                                         
2017-09-12 23:00:00         12  103.0         0  
2017-09-12 23:00:01         12  101.0         0  
2017-09-12 23:00:02         12  104.0         0  
2017-09-12 23:00:03         12  104.0         0  
2017-09-12 23:00:04         12  105.0         0  
...                        ...    ...       ...  
2017-11-10 23:59:54         10  210.0         0  
2017-11-10 23:59:55         10  210.0         0  
2017-11-10 23:59:56         10  219.0         0  
2017-11-10 23:59:57         10  216.0         0  
2017-11-10 23:59:58         10  215.0         0  

[5101192 rows x 9 columns]

In [4]:
house1_power_blk2_copy = house1_power_blk2.copy()
house2_power_blk1_copy = house2_power_blk1.copy()

In [5]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

In [6]:
house1_power_blk2

min         mean      max  load+1  hour  month  \
datetime                                                                
2016-03-06 00:00:00  473.0   473.000000    473.0   474.0     0      3   
2016-03-06 00:00:01  473.0   473.500000    474.0   476.0     0      3   
2016-03-06 00:00:02  473.0   474.333333    476.0   476.0     0      3   
2016-03-06 00:00:03  473.0   474.750000    476.0   475.0     0      3   
2016-03-06 00:00:04  473.0   474.800000    476.0   476.0     0      3   
...                    ...          ...      ...     ...   ...    ...   
2016-05-07 22:59:54  225.0  1104.073761  17206.0   604.0    22      5   
2016-05-07 22:59:55  225.0  1104.073669  17206.0   602.0    22      5   
2016-05-07 22:59:56  225.0  1104.073577  17206.0   602.0    22      5   
2016-05-07 22:59:57  225.0  1104.073485  17206.0   600.0    22      5   
2016-05-07 22:59:58  225.0  1104.073392  17206.0   603.0    22      5   

                     dayofweek  mains  activity  
datetime                                         
2016-03-06 00:00:00          6  473.0         0  
2016-03-06 00:00:01          6  474.0         0  
2016-03-06 00:00:02          6  476.0         0  
2016-03-06 00:00:03          6  476.0         0  
2016-03-06 00:00:04          6  475.0         0  
...                        ...    ...       ...  
2016-05-07 22:59:54          7  601.0         0  
2016-05-07 22:59:55          7  604.0         0  
2016-05-07 22:59:56          7  602.0         0  
2016-05-07 22:59:57          7  602.0         0  
2016-05-07 22:59:58          7  600.0         0  

[5439569 rows x 9 columns]

In [7]:
house2_power_blk1

min        mean     max  load+1  hour  month  \
datetime                                                              
2017-09-12 23:00:00  103.0  103.000000   103.0   101.0    23      9   
2017-09-12 23:00:01  101.0  102.000000   103.0   104.0    23      9   
2017-09-12 23:00:02  101.0  102.666667   104.0   104.0    23      9   
2017-09-12 23:00:03  101.0  103.000000   104.0   105.0    23      9   
2017-09-12 23:00:04  101.0  103.400000   105.0   107.0    23      9   
...                    ...         ...     ...     ...   ...    ...   
2017-11-10 23:59:54    1.0  343.545136  7753.0   210.0    23     11   
2017-11-10 23:59:55    1.0  343.545110  7753.0   219.0    23     11   
2017-11-10 23:59:56    1.0  343.545086  7753.0   216.0    23     11   
2017-11-10 23:59:57    1.0  343.545061  7753.0   215.0    23     11   
2017-11-10 23:59:58    1.0  343.545036  7753.0   209.0    23     11   

                     dayofweek  mains  activity  
datetime                                         
2017-09-12 23:00:00         12  103.0         0  
2017-09-12 23:00:01         12  101.0         0  
2017-09-12 23:00:02         12  104.0         0  
2017-09-12 23:00:03         12  104.0         0  
2017-09-12 23:00:04         12  105.0         0  
...                        ...    ...       ...  
2017-11-10 23:59:54         10  210.0         0  
2017-11-10 23:59:55         10  210.0         0  
2017-11-10 23:59:56         10  219.0         0  
2017-11-10 23:59:57         10  216.0         0  
2017-11-10 23:59:58         10  215.0         0  

[5101192 rows x 9 columns]

# export

In [ ]:
# compression_opts = dict(method='zip', archive_name='house2_power_blk1.csv')  
# house2_power_blk1.to_csv('house2_power_blk1_FE.zip', index=False, compression=compression_opts)

# compression_opts = dict(method='zip', archive_name='house1_power_blk2.csv')  
# house1_power_blk2.to_csv('house1_power_blk2_FE.zip', index=False, compression=compression_opts)

# import

In [ ]:
# house1_power_blk2 = pd.read_csv('data/house2_power_blk1_FE.zip',compression='zip')
# house2_power_blk1 = pd.read_csv('data/house1_power_blk2_FE.zip',compression='zip')

In [ ]:
# house1_power_blk2_copy = house1_power_blk2.copy()
# house2_power_blk1_copy = house2_power_blk1.copy()

In [ ]:
# house1_power_blk2 = house1_power_blk2_copy.copy()
# house2_power_blk1 = house2_power_blk1_copy.copy()

https://medium.com/data-science-at-microsoft/introduction-to-feature-engineering-for-time-series-forecasting-620aa55fcab0

# Train house 1 Test house 2

In [5]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_train = house1_power_blk2.iloc[:,-1]
X_train = house1_power_blk2.iloc[:,:-1]

y_test = house2_power_blk1.iloc[:,-1]
X_test = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore
    

https://runebook.dev/fr/docs/scikit_learn/auto_examples/preprocessing/plot_all_scaling
https://towardsdatascience.com/preprocessing-with-sklearn-a-complete-and-comprehensive-guide-670cb98fcfb9

In [ ]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), Normalizer(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "Normalizer", "MaxAbsScaler", "PowerTransformer"]

liste_classifier = [XGBClassifier(), HistGradientBoostingClassifier(), LGBMClassifier(), CatBoostClassifier()]
liste_classifier_name = ["XGBClassifier", "HistGradientBoostingClassifier", "LGBMClassifier", "CatBoostClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore


In [10]:
liste_acc

{'MinMaxScaler et XGBClassifier': 0.7108033743114573,
 'MinMaxScaler et HistGradientBoostingClassifier': 0.7450479992072901,
 'MinMaxScaler et LGBMClassifier': 0.7426873342354882,
 'MinMaxScaler et CatBoostClassifier': 0.7084894042156649,
 'StandardScaler et XGBClassifier': 0.7117892980123977,
 'StandardScaler et HistGradientBoostingClassifier': 0.7314774387456064,
 'StandardScaler et LGBMClassifier': 0.7390204996020825,
 'StandardScaler et CatBoostClassifier': 0.7120378471161961,
 'QuantileTransformer et XGBClassifier': 0.7215965088410498,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.7475531609213891,
 'QuantileTransformer et LGBMClassifier': 0.7420758887330963,
 'QuantileTransformer et CatBoostClassifier': 0.7078902758656063,
 'RobustScaler et XGBClassifier': 0.6762864851976323,
 'RobustScaler et HistGradientBoostingClassifier': 0.706439425623611,
 'RobustScaler et LGBMClassifier': 0.7071760648683747,
 'RobustScaler et CatBoostClassifier': 0.6496080847581858,
 'Normali

In [8]:
liste_fscore

{'MinMaxScaler et XGBClassifier': 0.6843545127531847,
 'MinMaxScaler et HistGradientBoostingClassifier': 0.7237298234575336,
 'MinMaxScaler et LGBMClassifier': 0.7207728349970046,
 'MinMaxScaler et CatBoostClassifier': 0.6796564592006893,
 'StandardScaler et XGBClassifier': 0.6960423189419419,
 'StandardScaler et HistGradientBoostingClassifier': 0.7320450462836604,
 'StandardScaler et LGBMClassifier': 0.7386024349482285,
 'StandardScaler et CatBoostClassifier': 0.6962818517429001,
 'QuantileTransformer et XGBClassifier': 0.7093369862403143,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.7414617561835315,
 'QuantileTransformer et LGBMClassifier': 0.7376148462485148,
 'QuantileTransformer et CatBoostClassifier': 0.6844781534425949,
 'RobustScaler et XGBClassifier': 0.6580195137116753,
 'RobustScaler et HistGradientBoostingClassifier': 0.6957644955892331,
 'RobustScaler et LGBMClassifier': 0.6963749869117486,
 'RobustScaler et CatBoostClassifier': 0.6307486773958211,
 'Normal

# Train house 2 Test house 1

In [11]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_test = house1_power_blk2.iloc[:,-1]
X_test = house1_power_blk2.iloc[:,:-1]

y_train = house2_power_blk1.iloc[:,-1]
X_train = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [12]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), Normalizer(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "Normalizer", "MaxAbsScaler", "PowerTransformer"]

liste_classifier = [XGBClassifier(), HistGradientBoostingClassifier(), LGBMClassifier(), CatBoostClassifier()]
liste_classifier_name = ["XGBClassifier", "HistGradientBoostingClassifier", "LGBMClassifier", "CatBoostClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0


C:\Users\julie\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[14:02:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
1
2
3
Learning rate set to 0.405527
0:	learn: 0.4920251	total: 618ms	remaining: 10m 16s
1:	learn: 0.4402042	total: 1.03s	remaining: 8m 35s
2:	learn: 0.4164623	total: 1.47s	remaining: 8m 8s
3:	learn: 0.4070666	total: 1.92s	remaining: 7m 56s
4:	learn: 0.3944806	total: 2.41s	remaining: 7m 59s
5:	learn: 0.3833144	total: 2.95s	remaining: 8m 9s
6:	learn: 0.3777813	total: 3.48s	remaining: 8m 13s
7:	learn: 0.3695967	total: 4.01s	remaining: 8m 17s
8:	learn: 0.3628064	total: 4.53s	remaining: 8m 18s
9:	learn: 0.3582899	total: 5.06s	remaining: 8m 20s
10:	learn: 0.3512285	total: 5.64s	remaining: 8m 27s
11:	learn: 0.3456545	total: 6.16s	remaining: 8m 26s
12:	learn: 0.3382059	total: 6.73s	remaini

151:	learn: 0.1487299	total: 1m 29s	remaining: 8m 16s
152:	learn: 0.1481112	total: 1m 29s	remaining: 8m 16s
153:	learn: 0.1477641	total: 1m 30s	remaining: 8m 16s
154:	learn: 0.1472754	total: 1m 31s	remaining: 8m 16s
155:	learn: 0.1469840	total: 1m 31s	remaining: 8m 16s
156:	learn: 0.1464454	total: 1m 32s	remaining: 8m 17s
157:	learn: 0.1461844	total: 1m 33s	remaining: 8m 16s
158:	learn: 0.1459556	total: 1m 33s	remaining: 8m 16s
159:	learn: 0.1455212	total: 1m 34s	remaining: 8m 16s
160:	learn: 0.1448147	total: 1m 35s	remaining: 8m 15s
161:	learn: 0.1445502	total: 1m 35s	remaining: 8m 15s
162:	learn: 0.1440434	total: 1m 36s	remaining: 8m 16s
163:	learn: 0.1437236	total: 1m 37s	remaining: 8m 15s
164:	learn: 0.1432670	total: 1m 37s	remaining: 8m 15s
165:	learn: 0.1428773	total: 1m 38s	remaining: 8m 15s
166:	learn: 0.1421909	total: 1m 39s	remaining: 8m 14s
167:	learn: 0.1412524	total: 1m 39s	remaining: 8m 14s
168:	learn: 0.1410015	total: 1m 40s	remaining: 8m 14s
169:	learn: 0.1407821	total:

305:	learn: 0.1076396	total: 3m 4s	remaining: 6m 59s
306:	learn: 0.1074105	total: 3m 5s	remaining: 6m 58s
307:	learn: 0.1073053	total: 3m 6s	remaining: 6m 58s
308:	learn: 0.1071839	total: 3m 6s	remaining: 6m 57s
309:	learn: 0.1070397	total: 3m 7s	remaining: 6m 57s
310:	learn: 0.1068905	total: 3m 8s	remaining: 6m 56s
311:	learn: 0.1067180	total: 3m 8s	remaining: 6m 56s
312:	learn: 0.1066368	total: 3m 9s	remaining: 6m 56s
313:	learn: 0.1064121	total: 3m 10s	remaining: 6m 56s
314:	learn: 0.1060969	total: 3m 11s	remaining: 6m 55s
315:	learn: 0.1059198	total: 3m 11s	remaining: 6m 55s
316:	learn: 0.1057862	total: 3m 12s	remaining: 6m 54s
317:	learn: 0.1056159	total: 3m 13s	remaining: 6m 54s
318:	learn: 0.1054582	total: 3m 13s	remaining: 6m 53s
319:	learn: 0.1052601	total: 3m 14s	remaining: 6m 53s
320:	learn: 0.1051283	total: 3m 15s	remaining: 6m 52s
321:	learn: 0.1050802	total: 3m 15s	remaining: 6m 51s
322:	learn: 0.1049224	total: 3m 16s	remaining: 6m 50s
323:	learn: 0.1048727	total: 3m 16s	

...

304:	learn: 0.1049028	total: 3m 8s	remaining: 7m 8s
305:	learn: 0.1047378	total: 3m 8s	remaining: 7m 7s
306:	learn: 0.1045683	total: 3m 9s	remaining: 7m 7s
307:	learn: 0.1043345	total: 3m 10s	remaining: 7m 7s
308:	learn: 0.1041603	total: 3m 10s	remaining: 7m 6s
309:	learn: 0.1040168	total: 3m 11s	remaining: 7m 5s
310:	learn: 0.1038461	total: 3m 11s	remaining: 7m 4s
311:	learn: 0.1037789	total: 3m 12s	remaining: 7m 4s
312:	learn: 0.1036133	total: 3m 13s	remaining: 7m 3s
313:	learn: 0.1034274	total: 3m 13s	remaining: 7m 3s
314:	learn: 0.1031732	total: 3m 14s	remaining: 7m 2s
315:	learn: 0.1030726	total: 3m 14s	remaining: 7m 1s
316:	learn: 0.1028098	total: 3m 15s	remaining: 7m
317:	learn: 0.1025472	total: 3m 16s	remaining: 7m
318:	learn: 0.1024630	total: 3m 16s	remaining: 7m
319:	learn: 0.1023638	total: 3m 17s	remaining: 6m 59s
320:	learn: 0.1022167	total: 3m 17s	remaining: 6m 58s
321:	learn: 0.1019695	total: 3m 18s	remaining: 6m 58s
322:	learn: 0.1019325	total: 3m 19s	remaining: 6m 57s
3

457:	learn: 0.0877398	total: 4m 43s	remaining: 5m 35s
458:	learn: 0.0876368	total: 4m 44s	remaining: 5m 35s
459:	learn: 0.0875621	total: 4m 45s	remaining: 5m 34s
460:	learn: 0.0875069	total: 4m 45s	remaining: 5m 34s
461:	learn: 0.0874279	total: 4m 46s	remaining: 5m 33s
462:	learn: 0.0873734	total: 4m 46s	remaining: 5m 32s
463:	learn: 0.0872914	total: 4m 47s	remaining: 5m 32s
464:	learn: 0.0872234	total: 4m 48s	remaining: 5m 31s
465:	learn: 0.0871847	total: 4m 48s	remaining: 5m 30s
466:	learn: 0.0871359	total: 4m 49s	remaining: 5m 30s
467:	learn: 0.0869946	total: 4m 49s	remaining: 5m 29s
468:	learn: 0.0869037	total: 4m 50s	remaining: 5m 28s
469:	learn: 0.0867745	total: 4m 50s	remaining: 5m 28s
470:	learn: 0.0867410	total: 4m 51s	remaining: 5m 27s
471:	learn: 0.0866991	total: 4m 51s	remaining: 5m 26s
472:	learn: 0.0866301	total: 4m 52s	remaining: 5m 25s
473:	learn: 0.0864464	total: 4m 53s	remaining: 5m 25s
474:	learn: 0.0863994	total: 4m 53s	remaining: 5m 24s
475:	learn: 0.0863612	total:

611:	learn: 0.0780777	total: 6m 15s	remaining: 3m 58s
612:	learn: 0.0779572	total: 6m 16s	remaining: 3m 57s
613:	learn: 0.0778344	total: 6m 16s	remaining: 3m 56s
614:	learn: 0.0777924	total: 6m 17s	remaining: 3m 56s
615:	learn: 0.0777650	total: 6m 17s	remaining: 3m 55s
616:	learn: 0.0777273	total: 6m 18s	remaining: 3m 54s
617:	learn: 0.0776789	total: 6m 19s	remaining: 3m 54s
618:	learn: 0.0776431	total: 6m 19s	remaining: 3m 53s
619:	learn: 0.0775492	total: 6m 20s	remaining: 3m 53s
620:	learn: 0.0774891	total: 6m 21s	remaining: 3m 52s
621:	learn: 0.0774390	total: 6m 21s	remaining: 3m 52s
622:	learn: 0.0774117	total: 6m 22s	remaining: 3m 51s
623:	learn: 0.0773703	total: 6m 23s	remaining: 3m 50s
624:	learn: 0.0773191	total: 6m 23s	remaining: 3m 50s
625:	learn: 0.0772453	total: 6m 24s	remaining: 3m 49s
626:	learn: 0.0772078	total: 6m 24s	remaining: 3m 48s
627:	learn: 0.0771897	total: 6m 25s	remaining: 3m 48s
628:	learn: 0.0771129	total: 6m 25s	remaining: 3m 47s
629:	learn: 0.0770930	total:

764:	learn: 0.0714765	total: 7m 47s	remaining: 2m 23s
765:	learn: 0.0714305	total: 7m 47s	remaining: 2m 22s
766:	learn: 0.0713877	total: 7m 48s	remaining: 2m 22s
767:	learn: 0.0713556	total: 7m 49s	remaining: 2m 21s
768:	learn: 0.0712934	total: 7m 49s	remaining: 2m 21s
769:	learn: 0.0712751	total: 7m 50s	remaining: 2m 20s
770:	learn: 0.0712389	total: 7m 51s	remaining: 2m 19s
771:	learn: 0.0711953	total: 7m 52s	remaining: 2m 19s
772:	learn: 0.0711713	total: 7m 52s	remaining: 2m 18s
773:	learn: 0.0711403	total: 7m 53s	remaining: 2m 18s
774:	learn: 0.0711130	total: 7m 54s	remaining: 2m 17s
775:	learn: 0.0710821	total: 7m 55s	remaining: 2m 17s
776:	learn: 0.0710010	total: 7m 55s	remaining: 2m 16s
777:	learn: 0.0709865	total: 7m 56s	remaining: 2m 16s
778:	learn: 0.0709370	total: 7m 57s	remaining: 2m 15s
779:	learn: 0.0708986	total: 7m 57s	remaining: 2m 14s
780:	learn: 0.0708748	total: 7m 58s	remaining: 2m 14s
781:	learn: 0.0708592	total: 7m 58s	remaining: 2m 13s
782:	learn: 0.0707947	total:

918:	learn: 0.0667291	total: 9m 18s	remaining: 49.2s
919:	learn: 0.0667127	total: 9m 19s	remaining: 48.6s
920:	learn: 0.0666889	total: 9m 19s	remaining: 48s
921:	learn: 0.0666756	total: 9m 20s	remaining: 47.4s
922:	learn: 0.0666382	total: 9m 20s	remaining: 46.8s
923:	learn: 0.0666118	total: 9m 21s	remaining: 46.2s
924:	learn: 0.0665719	total: 9m 21s	remaining: 45.6s
925:	learn: 0.0665496	total: 9m 22s	remaining: 45s
926:	learn: 0.0665229	total: 9m 23s	remaining: 44.4s
927:	learn: 0.0665045	total: 9m 24s	remaining: 43.8s
928:	learn: 0.0664950	total: 9m 25s	remaining: 43.2s
929:	learn: 0.0664351	total: 9m 26s	remaining: 42.6s
930:	learn: 0.0664156	total: 9m 26s	remaining: 42s
931:	learn: 0.0663969	total: 9m 28s	remaining: 41.5s
932:	learn: 0.0663743	total: 9m 28s	remaining: 40.9s
933:	learn: 0.0663625	total: 9m 29s	remaining: 40.2s
934:	learn: 0.0663480	total: 9m 30s	remaining: 39.6s
935:	learn: 0.0663250	total: 9m 31s	remaining: 39s
936:	learn: 0.0663017	total: 9m 31s	remaining: 38.4s
9

In [13]:
liste_acc

{'MinMaxScaler et XGBClassifier': 0.6909438029386072,
 'MinMaxScaler et HistGradientBoostingClassifier': 0.7151622601148908,
 'MinMaxScaler et LGBMClassifier': 0.7188439486300456,
 'MinMaxScaler et CatBoostClassifier': 0.7133620926246258,
 'StandardScaler et XGBClassifier': 0.6721378062225456,
 'StandardScaler et HistGradientBoostingClassifier': 0.7469448317177633,
 'StandardScaler et LGBMClassifier': 0.7402781545960239,
 'StandardScaler et CatBoostClassifier': 0.7097670505246617,
 'QuantileTransformer et XGBClassifier': 0.7034299042263064,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.7581784806374667,
 'QuantileTransformer et LGBMClassifier': 0.7600474555750891,
 'QuantileTransformer et CatBoostClassifier': 0.7174854426181175,
 'RobustScaler et XGBClassifier': 0.6876878972600914,
 'RobustScaler et HistGradientBoostingClassifier': 0.7114494024141809,
 'RobustScaler et LGBMClassifier': 0.718136858992957,
 'RobustScaler et CatBoostClassifier': 0.665419376490828,
 'Normaliz

In [14]:
liste_fscore

{'MinMaxScaler et XGBClassifier': 0.6436030177163782,
 'MinMaxScaler et HistGradientBoostingClassifier': 0.6685247592631415,
 'MinMaxScaler et LGBMClassifier': 0.6739799088130268,
 'MinMaxScaler et CatBoostClassifier': 0.6651065159452256,
 'StandardScaler et XGBClassifier': 0.6264683408878959,
 'StandardScaler et HistGradientBoostingClassifier': 0.6969490938339212,
 'StandardScaler et LGBMClassifier': 0.6893385347072843,
 'StandardScaler et CatBoostClassifier': 0.6615631346759613,
 'QuantileTransformer et XGBClassifier': 0.6597500224429885,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.7168917039087166,
 'QuantileTransformer et LGBMClassifier': 0.7190702476715295,
 'QuantileTransformer et CatBoostClassifier': 0.6730273982833012,
 'RobustScaler et XGBClassifier': 0.6422150302239176,
 'RobustScaler et HistGradientBoostingClassifier': 0.6684590784851037,
 'RobustScaler et LGBMClassifier': 0.6753959722864694,
 'RobustScaler et CatBoostClassifier': 0.6199518140498393,
 'Normal

https://towardsdatascience.com/kagglers-guide-to-lightgbm-hyperparameter-tuning-with-optuna-in-2021-ed048d9838b5

# Train house 2 Test house 1 - la nuit

In [7]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

house2_power_blk1 = house2_power_blk1.between_time('22:00', '5:59:59')
house1_power_blk2 = house1_power_blk2.between_time('22:00', '5:59:59')

In [8]:
taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_test = house1_power_blk2.iloc[:,-1]
X_test = house1_power_blk2.iloc[:,:-1]

y_train = house2_power_blk1.iloc[:,-1]
X_train = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [10]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "MaxAbsScaler", "PowerTransformer"]

liste_classifier = [HistGradientBoostingClassifier(), LGBMClassifier(), CatBoostClassifier()]
liste_classifier_name = ["HistGradientBoostingClassifier", "LGBMClassifier", "CatBoostClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0
1
2
Learning rate set to 0.246968
0:	learn: 0.4239267	total: 308ms	remaining: 5m 7s
1:	learn: 0.3094317	total: 435ms	remaining: 3m 36s
2:	learn: 0.2587223	total: 580ms	remaining: 3m 12s
3:	learn: 0.2226719	total: 710ms	remaining: 2m 56s
4:	learn: 0.2052410	total: 854ms	remaining: 2m 49s
5:	learn: 0.1976028	total: 985ms	remaining: 2m 43s
6:	learn: 0.1893881	total: 1.13s	remaining: 2m 40s
7:	learn: 0.1841512	total: 1.24s	remaining: 2m 34s
8:	learn: 0.1802913	total: 1.39s	remaining: 2m 32s
9:	learn: 0.1758987	total: 1.51s	remaining: 2m 29s
10:	learn: 0.1705514	total: 1.65s	remaining: 2m 28s
11:	learn: 0.1653866	total: 1.78s	remaining: 2m 26s
12:	learn: 0.1617689	total: 1.91s	remaining: 2m 24s
13:	learn: 0.1583276	total: 2.03s	remaining: 2m 23s
14:	learn: 0.1543111	total: 2.18s	remaining: 2m 23s
15:	learn: 0.1527346	total: 2.31s	remaining: 2m 21s
16:	learn: 0.1499769	total: 2.44s	remaining: 2m 21s
17:	learn: 0.1470806	total: 2.57s	remaining: 2m 20s
18:	learn: 0.1439201	total: 2.7s	remain

160:	learn: 0.0514307	total: 22.9s	remaining: 1m 59s
161:	learn: 0.0513685	total: 23s	remaining: 1m 59s
162:	learn: 0.0511025	total: 23.2s	remaining: 1m 59s
163:	learn: 0.0510426	total: 23.3s	remaining: 1m 58s
164:	learn: 0.0509884	total: 23.5s	remaining: 1m 58s
165:	learn: 0.0508199	total: 23.6s	remaining: 1m 58s
166:	learn: 0.0507539	total: 23.8s	remaining: 1m 58s
167:	learn: 0.0506798	total: 23.9s	remaining: 1m 58s
168:	learn: 0.0505284	total: 24.1s	remaining: 1m 58s
169:	learn: 0.0504271	total: 24.2s	remaining: 1m 58s
170:	learn: 0.0503509	total: 24.4s	remaining: 1m 58s
171:	learn: 0.0502235	total: 24.5s	remaining: 1m 57s
172:	learn: 0.0501134	total: 24.6s	remaining: 1m 57s
173:	learn: 0.0500086	total: 24.8s	remaining: 1m 57s
174:	learn: 0.0499109	total: 24.9s	remaining: 1m 57s
175:	learn: 0.0497592	total: 25.1s	remaining: 1m 57s
176:	learn: 0.0495870	total: 25.2s	remaining: 1m 57s
177:	learn: 0.0495187	total: 25.4s	remaining: 1m 57s
178:	learn: 0.0494774	total: 25.5s	remaining: 1m

316:	learn: 0.0403327	total: 47.3s	remaining: 1m 41s
317:	learn: 0.0403237	total: 47.5s	remaining: 1m 41s
318:	learn: 0.0402526	total: 47.6s	remaining: 1m 41s
319:	learn: 0.0402034	total: 47.7s	remaining: 1m 41s
320:	learn: 0.0401507	total: 47.9s	remaining: 1m 41s
321:	learn: 0.0401274	total: 48s	remaining: 1m 41s
322:	learn: 0.0400982	total: 48.2s	remaining: 1m 41s
323:	learn: 0.0400684	total: 48.4s	remaining: 1m 40s
324:	learn: 0.0400429	total: 48.5s	remaining: 1m 40s
325:	learn: 0.0400182	total: 48.6s	remaining: 1m 40s
326:	learn: 0.0400123	total: 48.8s	remaining: 1m 40s
327:	learn: 0.0399755	total: 48.9s	remaining: 1m 40s
328:	learn: 0.0399047	total: 49.1s	remaining: 1m 40s
329:	learn: 0.0398945	total: 49.2s	remaining: 1m 39s
330:	learn: 0.0398589	total: 49.4s	remaining: 1m 39s
331:	learn: 0.0398488	total: 49.5s	remaining: 1m 39s
332:	learn: 0.0398241	total: 49.7s	remaining: 1m 39s
333:	learn: 0.0397998	total: 49.8s	remaining: 1m 39s
334:	learn: 0.0397794	total: 50s	remaining: 1m 3

472:	learn: 0.0371455	total: 1m 10s	remaining: 1m 18s
473:	learn: 0.0371426	total: 1m 10s	remaining: 1m 18s
474:	learn: 0.0371288	total: 1m 10s	remaining: 1m 17s
475:	learn: 0.0371195	total: 1m 10s	remaining: 1m 17s
476:	learn: 0.0371159	total: 1m 10s	remaining: 1m 17s
477:	learn: 0.0370812	total: 1m 10s	remaining: 1m 17s
478:	learn: 0.0370535	total: 1m 11s	remaining: 1m 17s
479:	learn: 0.0370498	total: 1m 11s	remaining: 1m 17s
480:	learn: 0.0370469	total: 1m 11s	remaining: 1m 16s
481:	learn: 0.0370366	total: 1m 11s	remaining: 1m 16s
482:	learn: 0.0370280	total: 1m 11s	remaining: 1m 16s
483:	learn: 0.0370238	total: 1m 11s	remaining: 1m 16s
484:	learn: 0.0370208	total: 1m 11s	remaining: 1m 16s
485:	learn: 0.0370003	total: 1m 12s	remaining: 1m 16s
486:	learn: 0.0369982	total: 1m 12s	remaining: 1m 15s
487:	learn: 0.0369945	total: 1m 12s	remaining: 1m 15s
488:	learn: 0.0369754	total: 1m 12s	remaining: 1m 15s
489:	learn: 0.0369573	total: 1m 12s	remaining: 1m 15s
490:	learn: 0.0369492	total:

628:	learn: 0.0358469	total: 1m 33s	remaining: 54.9s
629:	learn: 0.0358469	total: 1m 33s	remaining: 54.7s
630:	learn: 0.0358229	total: 1m 33s	remaining: 54.6s
631:	learn: 0.0358141	total: 1m 33s	remaining: 54.4s
632:	learn: 0.0358141	total: 1m 33s	remaining: 54.3s
633:	learn: 0.0358111	total: 1m 33s	remaining: 54.1s
634:	learn: 0.0358111	total: 1m 33s	remaining: 54s
635:	learn: 0.0358080	total: 1m 34s	remaining: 53.8s
636:	learn: 0.0358044	total: 1m 34s	remaining: 53.7s
637:	learn: 0.0358008	total: 1m 34s	remaining: 53.5s
638:	learn: 0.0357950	total: 1m 34s	remaining: 53.4s
639:	learn: 0.0357931	total: 1m 34s	remaining: 53.2s
640:	learn: 0.0357853	total: 1m 34s	remaining: 53.1s
641:	learn: 0.0357769	total: 1m 34s	remaining: 52.9s
642:	learn: 0.0357724	total: 1m 35s	remaining: 52.8s
643:	learn: 0.0357628	total: 1m 35s	remaining: 52.7s
644:	learn: 0.0357627	total: 1m 35s	remaining: 52.5s
645:	learn: 0.0357587	total: 1m 35s	remaining: 52.4s
646:	learn: 0.0357311	total: 1m 35s	remaining: 5

...

314:	learn: 0.0402808	total: 45.2s	remaining: 1m 38s
315:	learn: 0.0402103	total: 45.4s	remaining: 1m 38s
316:	learn: 0.0401518	total: 45.5s	remaining: 1m 38s
317:	learn: 0.0401322	total: 45.7s	remaining: 1m 37s
318:	learn: 0.0401017	total: 45.8s	remaining: 1m 37s
319:	learn: 0.0400701	total: 46s	remaining: 1m 37s
320:	learn: 0.0400356	total: 46.1s	remaining: 1m 37s
321:	learn: 0.0400161	total: 46.3s	remaining: 1m 37s
322:	learn: 0.0400020	total: 46.4s	remaining: 1m 37s
323:	learn: 0.0399939	total: 46.6s	remaining: 1m 37s
324:	learn: 0.0399815	total: 46.7s	remaining: 1m 37s
325:	learn: 0.0399523	total: 46.9s	remaining: 1m 36s
326:	learn: 0.0399459	total: 47s	remaining: 1m 36s
327:	learn: 0.0399388	total: 47.2s	remaining: 1m 36s
328:	learn: 0.0398391	total: 47.3s	remaining: 1m 36s
329:	learn: 0.0398213	total: 47.5s	remaining: 1m 36s
330:	learn: 0.0397977	total: 47.6s	remaining: 1m 36s
331:	learn: 0.0397511	total: 47.8s	remaining: 1m 36s
332:	learn: 0.0397050	total: 47.9s	remaining: 1m 3

470:	learn: 0.0369074	total: 1m 9s	remaining: 1m 18s
471:	learn: 0.0369029	total: 1m 9s	remaining: 1m 17s
472:	learn: 0.0368816	total: 1m 9s	remaining: 1m 17s
473:	learn: 0.0368667	total: 1m 9s	remaining: 1m 17s
474:	learn: 0.0368632	total: 1m 10s	remaining: 1m 17s
475:	learn: 0.0368498	total: 1m 10s	remaining: 1m 17s
476:	learn: 0.0368380	total: 1m 10s	remaining: 1m 17s
477:	learn: 0.0368340	total: 1m 10s	remaining: 1m 17s
478:	learn: 0.0368283	total: 1m 10s	remaining: 1m 16s
479:	learn: 0.0368198	total: 1m 10s	remaining: 1m 16s
480:	learn: 0.0367804	total: 1m 11s	remaining: 1m 16s
481:	learn: 0.0367709	total: 1m 11s	remaining: 1m 16s
482:	learn: 0.0367656	total: 1m 11s	remaining: 1m 16s
483:	learn: 0.0367416	total: 1m 11s	remaining: 1m 16s
484:	learn: 0.0367197	total: 1m 11s	remaining: 1m 16s
485:	learn: 0.0367010	total: 1m 11s	remaining: 1m 16s
486:	learn: 0.0366840	total: 1m 12s	remaining: 1m 15s
487:	learn: 0.0366780	total: 1m 12s	remaining: 1m 15s
488:	learn: 0.0366731	total: 1m 

626:	learn: 0.0352323	total: 1m 34s	remaining: 56.1s
627:	learn: 0.0352125	total: 1m 34s	remaining: 56s
628:	learn: 0.0352071	total: 1m 34s	remaining: 55.8s
629:	learn: 0.0352029	total: 1m 34s	remaining: 55.7s
630:	learn: 0.0352004	total: 1m 34s	remaining: 55.5s
631:	learn: 0.0351964	total: 1m 35s	remaining: 55.4s
632:	learn: 0.0351937	total: 1m 35s	remaining: 55.3s
633:	learn: 0.0351900	total: 1m 35s	remaining: 55.1s
634:	learn: 0.0351744	total: 1m 35s	remaining: 55s
635:	learn: 0.0351717	total: 1m 35s	remaining: 54.8s
636:	learn: 0.0351695	total: 1m 35s	remaining: 54.7s
637:	learn: 0.0351650	total: 1m 36s	remaining: 54.5s
638:	learn: 0.0351564	total: 1m 36s	remaining: 54.4s
639:	learn: 0.0351555	total: 1m 36s	remaining: 54.2s
640:	learn: 0.0351369	total: 1m 36s	remaining: 54.1s
641:	learn: 0.0351357	total: 1m 36s	remaining: 54s
642:	learn: 0.0351209	total: 1m 36s	remaining: 53.8s
643:	learn: 0.0351150	total: 1m 37s	remaining: 53.7s
644:	learn: 0.0351131	total: 1m 37s	remaining: 53.5s

782:	learn: 0.0344067	total: 2m 1s	remaining: 33.6s
783:	learn: 0.0343989	total: 2m 1s	remaining: 33.4s
784:	learn: 0.0343989	total: 2m 1s	remaining: 33.3s
785:	learn: 0.0343989	total: 2m 1s	remaining: 33.1s
786:	learn: 0.0343961	total: 2m 1s	remaining: 33s
787:	learn: 0.0343961	total: 2m 1s	remaining: 32.8s
788:	learn: 0.0343944	total: 2m 2s	remaining: 32.7s
789:	learn: 0.0343908	total: 2m 2s	remaining: 32.5s
790:	learn: 0.0343840	total: 2m 2s	remaining: 32.4s
791:	learn: 0.0343779	total: 2m 2s	remaining: 32.2s
792:	learn: 0.0343715	total: 2m 2s	remaining: 32.1s
793:	learn: 0.0343628	total: 2m 2s	remaining: 31.9s
794:	learn: 0.0343590	total: 2m 3s	remaining: 31.8s
795:	learn: 0.0343542	total: 2m 3s	remaining: 31.6s
796:	learn: 0.0343515	total: 2m 3s	remaining: 31.5s
797:	learn: 0.0343515	total: 2m 3s	remaining: 31.3s
798:	learn: 0.0343514	total: 2m 3s	remaining: 31.1s
799:	learn: 0.0343488	total: 2m 3s	remaining: 31s
800:	learn: 0.0343459	total: 2m 4s	remaining: 30.8s
801:	learn: 0.03

939:	learn: 0.0340011	total: 2m 26s	remaining: 9.32s
940:	learn: 0.0339988	total: 2m 26s	remaining: 9.16s
941:	learn: 0.0339958	total: 2m 26s	remaining: 9.01s
942:	learn: 0.0339958	total: 2m 26s	remaining: 8.85s
943:	learn: 0.0339958	total: 2m 26s	remaining: 8.7s
944:	learn: 0.0339958	total: 2m 26s	remaining: 8.54s
945:	learn: 0.0339958	total: 2m 26s	remaining: 8.38s
946:	learn: 0.0339928	total: 2m 27s	remaining: 8.23s
947:	learn: 0.0339826	total: 2m 27s	remaining: 8.08s
948:	learn: 0.0339826	total: 2m 27s	remaining: 7.92s
949:	learn: 0.0339794	total: 2m 27s	remaining: 7.76s
950:	learn: 0.0339735	total: 2m 27s	remaining: 7.61s
951:	learn: 0.0339710	total: 2m 27s	remaining: 7.46s
952:	learn: 0.0339680	total: 2m 28s	remaining: 7.3s
953:	learn: 0.0339597	total: 2m 28s	remaining: 7.15s
954:	learn: 0.0339574	total: 2m 28s	remaining: 6.99s
955:	learn: 0.0339548	total: 2m 28s	remaining: 6.84s
956:	learn: 0.0339548	total: 2m 28s	remaining: 6.68s
957:	learn: 0.0339522	total: 2m 28s	remaining: 6

In [11]:
liste_acc

{'MinMaxScaler et HistGradientBoostingClassifier': 0.8420638448858099,
 'MinMaxScaler et LGBMClassifier': 0.8410074028258306,
 'MinMaxScaler et CatBoostClassifier': 0.8515723756692503,
 'StandardScaler et HistGradientBoostingClassifier': 0.8331373788860694,
 'StandardScaler et LGBMClassifier': 0.8381274523068597,
 'StandardScaler et CatBoostClassifier': 0.8503226483395415,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.8611609817787215,
 'QuantileTransformer et LGBMClassifier': 0.8561692516270478,
 'QuantileTransformer et CatBoostClassifier': 0.8525796680463553,
 'RobustScaler et HistGradientBoostingClassifier': 0.7821962176833932,
 'RobustScaler et LGBMClassifier': 0.789331757598182,
 'RobustScaler et CatBoostClassifier': 0.7883139725921487,
 'MaxAbsScaler et HistGradientBoostingClassifier': 0.8331583641439257,
 'MaxAbsScaler et LGBMClassifier': 0.8239154625454566,
 'MaxAbsScaler et CatBoostClassifier': 0.8426271333861647,
 'PowerTransformer et HistGradientBoostingClassif

In [12]:
liste_fscore

{'MinMaxScaler et HistGradientBoostingClassifier': 0.5442611657107284,
 'MinMaxScaler et LGBMClassifier': 0.5425376171473145,
 'MinMaxScaler et CatBoostClassifier': 0.5623187831431887,
 'StandardScaler et HistGradientBoostingClassifier': 0.5107706539797614,
 'StandardScaler et LGBMClassifier': 0.5266017385705087,
 'StandardScaler et CatBoostClassifier': 0.5465561629662348,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.5814176031336422,
 'QuantileTransformer et LGBMClassifier': 0.5655245847114692,
 'QuantileTransformer et CatBoostClassifier': 0.5482075744434808,
 'RobustScaler et HistGradientBoostingClassifier': 0.38460304534891315,
 'RobustScaler et LGBMClassifier': 0.40768686792401015,
 'RobustScaler et CatBoostClassifier': 0.39061547353685727,
 'MaxAbsScaler et HistGradientBoostingClassifier': 0.5268685118112622,
 'MaxAbsScaler et LGBMClassifier': 0.5134207459323955,
 'MaxAbsScaler et CatBoostClassifier': 0.5482181490118192,
 'PowerTransformer et HistGradientBoostingCla

# Train house 2 Test house 1 - le jour

In [35]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

house2_power_blk1 = house2_power_blk1.between_time('6:00:00', '21:59:59')
house1_power_blk2 = house1_power_blk2.between_time('6:00:00', '21:59:59')

In [36]:
taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_test = house1_power_blk2.iloc[:,-1]
X_test = house1_power_blk2.iloc[:,:-1]

y_train = house2_power_blk1.iloc[:,-1]
X_train = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [37]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "MaxAbsScaler", "PowerTransformer"]

liste_classifier = [HistGradientBoostingClassifier(), LGBMClassifier(), CatBoostClassifier()]
liste_classifier_name = ["HistGradientBoostingClassifier", "LGBMClassifier", "CatBoostClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0
1
2
Learning rate set to 0.331732
0:	learn: 0.5284390	total: 263ms	remaining: 4m 22s
1:	learn: 0.4679119	total: 556ms	remaining: 4m 37s
2:	learn: 0.4423416	total: 871ms	remaining: 4m 49s
3:	learn: 0.4272060	total: 1.15s	remaining: 4m 47s
4:	learn: 0.4142835	total: 1.43s	remaining: 4m 45s
5:	learn: 0.4011103	total: 1.72s	remaining: 4m 45s
6:	learn: 0.3955222	total: 2.01s	remaining: 4m 45s
7:	learn: 0.3886363	total: 2.3s	remaining: 4m 44s
8:	learn: 0.3827673	total: 2.62s	remaining: 4m 48s
9:	learn: 0.3752307	total: 2.95s	remaining: 4m 51s
10:	learn: 0.3686485	total: 3.27s	remaining: 4m 54s
11:	learn: 0.3651976	total: 3.58s	remaining: 4m 55s
12:	learn: 0.3620831	total: 3.89s	remaining: 4m 55s
13:	learn: 0.3587764	total: 4.18s	remaining: 4m 54s
14:	learn: 0.3532673	total: 4.49s	remaining: 4m 54s
15:	learn: 0.3488356	total: 4.81s	remaining: 4m 56s
16:	learn: 0.3422839	total: 5.13s	remaining: 4m 56s
17:	learn: 0.3399971	total: 5.46s	remaining: 4m 57s
18:	learn: 0.3342681	total: 5.79s	remai

158:	learn: 0.1560101	total: 56.5s	remaining: 4m 59s
159:	learn: 0.1557886	total: 56.9s	remaining: 4m 58s
160:	learn: 0.1553008	total: 57.3s	remaining: 4m 58s
161:	learn: 0.1545804	total: 57.6s	remaining: 4m 58s
162:	learn: 0.1540842	total: 58s	remaining: 4m 57s
163:	learn: 0.1533589	total: 58.4s	remaining: 4m 57s
164:	learn: 0.1529509	total: 58.7s	remaining: 4m 57s
165:	learn: 0.1525617	total: 59.1s	remaining: 4m 57s
166:	learn: 0.1522257	total: 59.5s	remaining: 4m 56s
167:	learn: 0.1518298	total: 59.9s	remaining: 4m 56s
168:	learn: 0.1514437	total: 1m	remaining: 4m 56s
169:	learn: 0.1506834	total: 1m	remaining: 4m 56s
170:	learn: 0.1500261	total: 1m 1s	remaining: 4m 55s
171:	learn: 0.1494840	total: 1m 1s	remaining: 4m 55s
172:	learn: 0.1490580	total: 1m 1s	remaining: 4m 55s
173:	learn: 0.1486226	total: 1m 2s	remaining: 4m 55s
174:	learn: 0.1483746	total: 1m 2s	remaining: 4m 55s
175:	learn: 0.1480350	total: 1m 3s	remaining: 4m 55s
176:	learn: 0.1472949	total: 1m 3s	remaining: 4m 54s
1

311:	learn: 0.1088904	total: 1m 53s	remaining: 4m 10s
312:	learn: 0.1087327	total: 1m 54s	remaining: 4m 10s
313:	learn: 0.1085270	total: 1m 54s	remaining: 4m 10s
314:	learn: 0.1084347	total: 1m 54s	remaining: 4m 9s
315:	learn: 0.1082823	total: 1m 55s	remaining: 4m 9s
316:	learn: 0.1080980	total: 1m 55s	remaining: 4m 8s
317:	learn: 0.1079076	total: 1m 55s	remaining: 4m 8s
318:	learn: 0.1077029	total: 1m 56s	remaining: 4m 8s
319:	learn: 0.1075609	total: 1m 56s	remaining: 4m 8s
320:	learn: 0.1074695	total: 1m 57s	remaining: 4m 7s
321:	learn: 0.1072909	total: 1m 57s	remaining: 4m 7s
322:	learn: 0.1069212	total: 1m 57s	remaining: 4m 6s
323:	learn: 0.1067463	total: 1m 58s	remaining: 4m 6s
324:	learn: 0.1064835	total: 1m 58s	remaining: 4m 6s
325:	learn: 0.1061053	total: 1m 58s	remaining: 4m 5s
326:	learn: 0.1058976	total: 1m 59s	remaining: 4m 5s
327:	learn: 0.1058003	total: 1m 59s	remaining: 4m 5s
328:	learn: 0.1055965	total: 2m	remaining: 4m 5s
329:	learn: 0.1054503	total: 2m	remaining: 4m 4

465:	learn: 0.0909864	total: 2m 51s	remaining: 3m 16s
466:	learn: 0.0909331	total: 2m 51s	remaining: 3m 15s
467:	learn: 0.0908820	total: 2m 51s	remaining: 3m 15s
468:	learn: 0.0908405	total: 2m 52s	remaining: 3m 14s
469:	learn: 0.0907579	total: 2m 52s	remaining: 3m 14s
470:	learn: 0.0907231	total: 2m 52s	remaining: 3m 14s
471:	learn: 0.0906917	total: 2m 53s	remaining: 3m 13s
472:	learn: 0.0905743	total: 2m 53s	remaining: 3m 13s
473:	learn: 0.0905417	total: 2m 53s	remaining: 3m 13s
474:	learn: 0.0904066	total: 2m 54s	remaining: 3m 12s
475:	learn: 0.0902936	total: 2m 54s	remaining: 3m 12s
476:	learn: 0.0901964	total: 2m 55s	remaining: 3m 12s
477:	learn: 0.0901655	total: 2m 55s	remaining: 3m 11s
478:	learn: 0.0900722	total: 2m 55s	remaining: 3m 11s
479:	learn: 0.0899902	total: 2m 56s	remaining: 3m 10s
480:	learn: 0.0898597	total: 2m 56s	remaining: 3m 10s
481:	learn: 0.0897702	total: 2m 56s	remaining: 3m 10s
482:	learn: 0.0896642	total: 2m 57s	remaining: 3m 9s
483:	learn: 0.0895288	total: 

619:	learn: 0.0813899	total: 3m 49s	remaining: 2m 20s
620:	learn: 0.0813653	total: 3m 49s	remaining: 2m 20s
621:	learn: 0.0813007	total: 3m 49s	remaining: 2m 19s
622:	learn: 0.0812753	total: 3m 50s	remaining: 2m 19s
623:	learn: 0.0812048	total: 3m 50s	remaining: 2m 18s
624:	learn: 0.0811527	total: 3m 50s	remaining: 2m 18s
625:	learn: 0.0811371	total: 3m 51s	remaining: 2m 18s
626:	learn: 0.0811108	total: 3m 51s	remaining: 2m 17s
627:	learn: 0.0810758	total: 3m 51s	remaining: 2m 17s
628:	learn: 0.0810473	total: 3m 52s	remaining: 2m 16s
629:	learn: 0.0808935	total: 3m 52s	remaining: 2m 16s
630:	learn: 0.0808343	total: 3m 52s	remaining: 2m 16s
631:	learn: 0.0807885	total: 3m 53s	remaining: 2m 15s
632:	learn: 0.0806742	total: 3m 53s	remaining: 2m 15s
633:	learn: 0.0806611	total: 3m 54s	remaining: 2m 15s
634:	learn: 0.0806281	total: 3m 54s	remaining: 2m 14s
635:	learn: 0.0805715	total: 3m 54s	remaining: 2m 14s
636:	learn: 0.0805324	total: 3m 55s	remaining: 2m 14s
637:	learn: 0.0804847	total:

...

259:	learn: 0.1193045	total: 1m 30s	remaining: 4m 17s
260:	learn: 0.1189713	total: 1m 30s	remaining: 4m 17s
261:	learn: 0.1187880	total: 1m 31s	remaining: 4m 17s
262:	learn: 0.1186326	total: 1m 31s	remaining: 4m 17s
263:	learn: 0.1183753	total: 1m 32s	remaining: 4m 16s
264:	learn: 0.1181079	total: 1m 32s	remaining: 4m 16s
265:	learn: 0.1179461	total: 1m 32s	remaining: 4m 16s
266:	learn: 0.1176890	total: 1m 33s	remaining: 4m 15s
267:	learn: 0.1175057	total: 1m 33s	remaining: 4m 15s
268:	learn: 0.1173031	total: 1m 33s	remaining: 4m 14s
269:	learn: 0.1171380	total: 1m 34s	remaining: 4m 14s
270:	learn: 0.1168568	total: 1m 34s	remaining: 4m 14s
271:	learn: 0.1166888	total: 1m 34s	remaining: 4m 13s
272:	learn: 0.1165571	total: 1m 35s	remaining: 4m 13s
273:	learn: 0.1164240	total: 1m 35s	remaining: 4m 13s
274:	learn: 0.1163023	total: 1m 35s	remaining: 4m 12s
275:	learn: 0.1160350	total: 1m 36s	remaining: 4m 12s
276:	learn: 0.1158665	total: 1m 36s	remaining: 4m 11s
277:	learn: 0.1156809	total:

413:	learn: 0.0959767	total: 2m 29s	remaining: 3m 30s
414:	learn: 0.0958333	total: 2m 29s	remaining: 3m 30s
415:	learn: 0.0957561	total: 2m 29s	remaining: 3m 30s
416:	learn: 0.0954963	total: 2m 30s	remaining: 3m 29s
417:	learn: 0.0954204	total: 2m 30s	remaining: 3m 29s
418:	learn: 0.0953438	total: 2m 30s	remaining: 3m 29s
419:	learn: 0.0950775	total: 2m 31s	remaining: 3m 28s
420:	learn: 0.0949373	total: 2m 31s	remaining: 3m 28s
421:	learn: 0.0948662	total: 2m 31s	remaining: 3m 28s
422:	learn: 0.0946840	total: 2m 32s	remaining: 3m 27s
423:	learn: 0.0946354	total: 2m 32s	remaining: 3m 27s
424:	learn: 0.0945421	total: 2m 33s	remaining: 3m 27s
425:	learn: 0.0944851	total: 2m 33s	remaining: 3m 26s
426:	learn: 0.0943425	total: 2m 33s	remaining: 3m 26s
427:	learn: 0.0942268	total: 2m 34s	remaining: 3m 26s
428:	learn: 0.0939806	total: 2m 34s	remaining: 3m 25s
429:	learn: 0.0938776	total: 2m 34s	remaining: 3m 25s
430:	learn: 0.0937546	total: 2m 35s	remaining: 3m 24s
431:	learn: 0.0936705	total:

567:	learn: 0.0838293	total: 3m 21s	remaining: 2m 32s
568:	learn: 0.0838082	total: 3m 21s	remaining: 2m 32s
569:	learn: 0.0837116	total: 3m 21s	remaining: 2m 32s
570:	learn: 0.0836473	total: 3m 22s	remaining: 2m 31s
571:	learn: 0.0836156	total: 3m 22s	remaining: 2m 31s
572:	learn: 0.0835821	total: 3m 22s	remaining: 2m 31s
573:	learn: 0.0835184	total: 3m 23s	remaining: 2m 30s
574:	learn: 0.0834421	total: 3m 23s	remaining: 2m 30s
575:	learn: 0.0834059	total: 3m 23s	remaining: 2m 30s
576:	learn: 0.0833541	total: 3m 24s	remaining: 2m 29s
577:	learn: 0.0833031	total: 3m 24s	remaining: 2m 29s
578:	learn: 0.0832619	total: 3m 25s	remaining: 2m 29s
579:	learn: 0.0831932	total: 3m 25s	remaining: 2m 28s
580:	learn: 0.0831217	total: 3m 25s	remaining: 2m 28s
581:	learn: 0.0830835	total: 3m 26s	remaining: 2m 28s
582:	learn: 0.0830407	total: 3m 26s	remaining: 2m 27s
583:	learn: 0.0830074	total: 3m 26s	remaining: 2m 27s
584:	learn: 0.0829121	total: 3m 27s	remaining: 2m 27s
585:	learn: 0.0828664	total:

720:	learn: 0.0770059	total: 4m 17s	remaining: 1m 39s
721:	learn: 0.0769557	total: 4m 17s	remaining: 1m 39s
722:	learn: 0.0769299	total: 4m 18s	remaining: 1m 38s
723:	learn: 0.0768957	total: 4m 18s	remaining: 1m 38s
724:	learn: 0.0768604	total: 4m 18s	remaining: 1m 38s
725:	learn: 0.0767783	total: 4m 19s	remaining: 1m 37s
726:	learn: 0.0767237	total: 4m 19s	remaining: 1m 37s
727:	learn: 0.0767011	total: 4m 20s	remaining: 1m 37s
728:	learn: 0.0766827	total: 4m 20s	remaining: 1m 36s
729:	learn: 0.0766680	total: 4m 20s	remaining: 1m 36s
730:	learn: 0.0766542	total: 4m 21s	remaining: 1m 36s
731:	learn: 0.0766123	total: 4m 21s	remaining: 1m 35s
732:	learn: 0.0765671	total: 4m 22s	remaining: 1m 35s
733:	learn: 0.0765149	total: 4m 23s	remaining: 1m 35s
734:	learn: 0.0764751	total: 4m 23s	remaining: 1m 35s
735:	learn: 0.0764511	total: 4m 24s	remaining: 1m 34s
736:	learn: 0.0764114	total: 4m 24s	remaining: 1m 34s
737:	learn: 0.0763939	total: 4m 25s	remaining: 1m 34s
738:	learn: 0.0763715	total:

874:	learn: 0.0719524	total: 5m 18s	remaining: 45.4s
875:	learn: 0.0719385	total: 5m 18s	remaining: 45.1s
876:	learn: 0.0719005	total: 5m 18s	remaining: 44.7s
877:	learn: 0.0718881	total: 5m 19s	remaining: 44.3s
878:	learn: 0.0718730	total: 5m 19s	remaining: 44s
879:	learn: 0.0718537	total: 5m 19s	remaining: 43.6s
880:	learn: 0.0718348	total: 5m 20s	remaining: 43.2s
881:	learn: 0.0718197	total: 5m 20s	remaining: 42.9s
882:	learn: 0.0717787	total: 5m 21s	remaining: 42.6s
883:	learn: 0.0717567	total: 5m 21s	remaining: 42.2s
884:	learn: 0.0717446	total: 5m 22s	remaining: 41.9s
885:	learn: 0.0717388	total: 5m 22s	remaining: 41.5s
886:	learn: 0.0717111	total: 5m 23s	remaining: 41.2s
887:	learn: 0.0716978	total: 5m 23s	remaining: 40.8s
888:	learn: 0.0716652	total: 5m 23s	remaining: 40.4s
889:	learn: 0.0716404	total: 5m 24s	remaining: 40.1s
890:	learn: 0.0716353	total: 5m 24s	remaining: 39.7s
891:	learn: 0.0716109	total: 5m 24s	remaining: 39.3s
892:	learn: 0.0715735	total: 5m 25s	remaining: 3

In [38]:
liste_acc

{'MinMaxScaler et HistGradientBoostingClassifier': 0.6769120920729701,
 'MinMaxScaler et LGBMClassifier': 0.6769165012756374,
 'MinMaxScaler et CatBoostClassifier': 0.6339309088965034,
 'StandardScaler et HistGradientBoostingClassifier': 0.6667954521279088,
 'StandardScaler et LGBMClassifier': 0.6806668037193829,
 'StandardScaler et CatBoostClassifier': 0.6406665171212095,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.6869501930955193,
 'QuantileTransformer et LGBMClassifier': 0.6893860019940619,
 'QuantileTransformer et CatBoostClassifier': 0.6697780021572024,
 'RobustScaler et HistGradientBoostingClassifier': 0.6894245825174012,
 'RobustScaler et LGBMClassifier': 0.696660910820018,
 'RobustScaler et CatBoostClassifier': 0.672105785590395,
 'MaxAbsScaler et HistGradientBoostingClassifier': 0.674222754021055,
 'MaxAbsScaler et LGBMClassifier': 0.6729239682603546,
 'MaxAbsScaler et CatBoostClassifier': 0.6457382024893256,
 'PowerTransformer et HistGradientBoostingClassifie

In [39]:
liste_fscore

{'MinMaxScaler et HistGradientBoostingClassifier': 0.7293388431342023,
 'MinMaxScaler et LGBMClassifier': 0.7277750637748577,
 'MinMaxScaler et CatBoostClassifier': 0.6881880439646876,
 'StandardScaler et HistGradientBoostingClassifier': 0.7550182028942577,
 'StandardScaler et LGBMClassifier': 0.7610001593931749,
 'StandardScaler et CatBoostClassifier': 0.6995755327297688,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.7519263399904226,
 'QuantileTransformer et LGBMClassifier': 0.7552240150224201,
 'QuantileTransformer et CatBoostClassifier': 0.7261747154232322,
 'RobustScaler et HistGradientBoostingClassifier': 0.7450982876240677,
 'RobustScaler et LGBMClassifier': 0.7585995853159405,
 'RobustScaler et CatBoostClassifier': 0.7221265251952677,
 'MaxAbsScaler et HistGradientBoostingClassifier': 0.7152264360004437,
 'MaxAbsScaler et LGBMClassifier': 0.7132079608235137,
 'MaxAbsScaler et CatBoostClassifier': 0.6924154240612899,
 'PowerTransformer et HistGradientBoostingClassi

# Train house 1 Test house 2 - la nuit

In [24]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

house2_power_blk1 = house2_power_blk1.between_time('22:00', '5:59:59')
house1_power_blk2 = house1_power_blk2.between_time('22:00', '5:59:59')

In [25]:
taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_train = house1_power_blk2.iloc[:,-1]
X_train = house1_power_blk2.iloc[:,:-1]

y_test = house2_power_blk1.iloc[:,-1]
X_test = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [26]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "MaxAbsScaler", "PowerTransformer"]

liste_classifier = [HistGradientBoostingClassifier(), LGBMClassifier(), CatBoostClassifier()]
liste_classifier_name = ["HistGradientBoostingClassifier", "LGBMClassifier", "CatBoostClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0
1
2
Learning rate set to 0.253539
0:	learn: 0.3955183	total: 153ms	remaining: 2m 33s
1:	learn: 0.2766588	total: 296ms	remaining: 2m 27s
2:	learn: 0.2350256	total: 440ms	remaining: 2m 26s
3:	learn: 0.2123539	total: 592ms	remaining: 2m 27s
4:	learn: 0.1948234	total: 735ms	remaining: 2m 26s
5:	learn: 0.1855632	total: 873ms	remaining: 2m 24s
6:	learn: 0.1763402	total: 1.02s	remaining: 2m 24s
7:	learn: 0.1704941	total: 1.21s	remaining: 2m 29s
8:	learn: 0.1636217	total: 1.38s	remaining: 2m 32s
9:	learn: 0.1611709	total: 1.54s	remaining: 2m 32s
10:	learn: 0.1568143	total: 1.7s	remaining: 2m 33s
11:	learn: 0.1523538	total: 1.86s	remaining: 2m 33s
12:	learn: 0.1473761	total: 2.02s	remaining: 2m 33s
13:	learn: 0.1447189	total: 2.17s	remaining: 2m 33s
14:	learn: 0.1412266	total: 2.33s	remaining: 2m 32s
15:	learn: 0.1382691	total: 2.48s	remaining: 2m 32s
16:	learn: 0.1325173	total: 2.64s	remaining: 2m 32s
17:	learn: 0.1308035	total: 2.8s	remaining: 2m 32s
18:	learn: 0.1283924	total: 2.99s	remain

158:	learn: 0.0497908	total: 26.7s	remaining: 2m 21s
159:	learn: 0.0496693	total: 26.9s	remaining: 2m 21s
160:	learn: 0.0495407	total: 27.1s	remaining: 2m 21s
161:	learn: 0.0494646	total: 27.2s	remaining: 2m 20s
162:	learn: 0.0493744	total: 27.4s	remaining: 2m 20s
163:	learn: 0.0491546	total: 27.6s	remaining: 2m 20s
164:	learn: 0.0490746	total: 27.7s	remaining: 2m 20s
165:	learn: 0.0489659	total: 27.9s	remaining: 2m 20s
166:	learn: 0.0488844	total: 28.2s	remaining: 2m 20s
167:	learn: 0.0487835	total: 28.3s	remaining: 2m 20s
168:	learn: 0.0485926	total: 28.5s	remaining: 2m 20s
169:	learn: 0.0481805	total: 28.7s	remaining: 2m 20s
170:	learn: 0.0480014	total: 28.9s	remaining: 2m 20s
171:	learn: 0.0478818	total: 29.1s	remaining: 2m 20s
172:	learn: 0.0477934	total: 29.3s	remaining: 2m 19s
173:	learn: 0.0476029	total: 29.4s	remaining: 2m 19s
174:	learn: 0.0474817	total: 29.6s	remaining: 2m 19s
175:	learn: 0.0473721	total: 29.8s	remaining: 2m 19s
176:	learn: 0.0473146	total: 30s	remaining: 2m

315:	learn: 0.0378323	total: 54.8s	remaining: 1m 58s
316:	learn: 0.0377663	total: 54.9s	remaining: 1m 58s
317:	learn: 0.0377170	total: 55.1s	remaining: 1m 58s
318:	learn: 0.0376897	total: 55.3s	remaining: 1m 57s
319:	learn: 0.0376669	total: 55.4s	remaining: 1m 57s
320:	learn: 0.0376414	total: 55.6s	remaining: 1m 57s
321:	learn: 0.0375325	total: 55.8s	remaining: 1m 57s
322:	learn: 0.0374568	total: 55.9s	remaining: 1m 57s
323:	learn: 0.0374368	total: 56.1s	remaining: 1m 57s
324:	learn: 0.0374081	total: 56.3s	remaining: 1m 56s
325:	learn: 0.0373734	total: 56.4s	remaining: 1m 56s
326:	learn: 0.0373324	total: 56.6s	remaining: 1m 56s
327:	learn: 0.0372777	total: 56.7s	remaining: 1m 56s
328:	learn: 0.0372247	total: 56.9s	remaining: 1m 56s
329:	learn: 0.0371809	total: 57.1s	remaining: 1m 55s
330:	learn: 0.0371332	total: 57.3s	remaining: 1m 55s
331:	learn: 0.0370867	total: 57.4s	remaining: 1m 55s
332:	learn: 0.0370779	total: 57.6s	remaining: 1m 55s
333:	learn: 0.0370527	total: 57.8s	remaining: 

469:	learn: 0.0326483	total: 1m 22s	remaining: 1m 32s
470:	learn: 0.0326070	total: 1m 22s	remaining: 1m 32s
471:	learn: 0.0325927	total: 1m 22s	remaining: 1m 32s
472:	learn: 0.0325697	total: 1m 23s	remaining: 1m 32s
473:	learn: 0.0325581	total: 1m 23s	remaining: 1m 32s
474:	learn: 0.0325132	total: 1m 23s	remaining: 1m 32s
475:	learn: 0.0324991	total: 1m 23s	remaining: 1m 32s
476:	learn: 0.0324849	total: 1m 23s	remaining: 1m 31s
477:	learn: 0.0324559	total: 1m 24s	remaining: 1m 31s
478:	learn: 0.0324453	total: 1m 24s	remaining: 1m 31s
479:	learn: 0.0324295	total: 1m 24s	remaining: 1m 31s
480:	learn: 0.0324116	total: 1m 24s	remaining: 1m 31s
481:	learn: 0.0323945	total: 1m 24s	remaining: 1m 31s
482:	learn: 0.0323667	total: 1m 25s	remaining: 1m 31s
483:	learn: 0.0323513	total: 1m 25s	remaining: 1m 30s
484:	learn: 0.0323418	total: 1m 25s	remaining: 1m 30s
485:	learn: 0.0323164	total: 1m 25s	remaining: 1m 30s
486:	learn: 0.0323015	total: 1m 25s	remaining: 1m 30s
487:	learn: 0.0322885	total:

622:	learn: 0.0301732	total: 1m 52s	remaining: 1m 8s
623:	learn: 0.0301483	total: 1m 52s	remaining: 1m 7s
624:	learn: 0.0301439	total: 1m 52s	remaining: 1m 7s
625:	learn: 0.0301340	total: 1m 53s	remaining: 1m 7s
626:	learn: 0.0301262	total: 1m 53s	remaining: 1m 7s
627:	learn: 0.0301083	total: 1m 53s	remaining: 1m 7s
628:	learn: 0.0300920	total: 1m 53s	remaining: 1m 7s
629:	learn: 0.0300807	total: 1m 54s	remaining: 1m 7s
630:	learn: 0.0300715	total: 1m 54s	remaining: 1m 6s
631:	learn: 0.0300551	total: 1m 54s	remaining: 1m 6s
632:	learn: 0.0300482	total: 1m 54s	remaining: 1m 6s
633:	learn: 0.0300329	total: 1m 55s	remaining: 1m 6s
634:	learn: 0.0300255	total: 1m 55s	remaining: 1m 6s
635:	learn: 0.0300113	total: 1m 55s	remaining: 1m 6s
636:	learn: 0.0300023	total: 1m 55s	remaining: 1m 5s
637:	learn: 0.0299892	total: 1m 55s	remaining: 1m 5s
638:	learn: 0.0299791	total: 1m 55s	remaining: 1m 5s
639:	learn: 0.0299662	total: 1m 56s	remaining: 1m 5s
640:	learn: 0.0299477	total: 1m 56s	remaining:

...

313:	learn: 0.0373432	total: 1m 2s	remaining: 2m 17s
314:	learn: 0.0373036	total: 1m 2s	remaining: 2m 16s
315:	learn: 0.0372742	total: 1m 3s	remaining: 2m 16s
316:	learn: 0.0372287	total: 1m 3s	remaining: 2m 16s
317:	learn: 0.0372062	total: 1m 3s	remaining: 2m 16s
318:	learn: 0.0371720	total: 1m 3s	remaining: 2m 15s
319:	learn: 0.0371113	total: 1m 3s	remaining: 2m 15s
320:	learn: 0.0370908	total: 1m 4s	remaining: 2m 15s
321:	learn: 0.0370704	total: 1m 4s	remaining: 2m 15s
322:	learn: 0.0370386	total: 1m 4s	remaining: 2m 14s
323:	learn: 0.0369714	total: 1m 4s	remaining: 2m 14s
324:	learn: 0.0369278	total: 1m 4s	remaining: 2m 14s
325:	learn: 0.0369186	total: 1m 4s	remaining: 2m 14s
326:	learn: 0.0369054	total: 1m 5s	remaining: 2m 14s
327:	learn: 0.0368702	total: 1m 5s	remaining: 2m 13s
328:	learn: 0.0368224	total: 1m 5s	remaining: 2m 13s
329:	learn: 0.0367675	total: 1m 5s	remaining: 2m 13s
330:	learn: 0.0367528	total: 1m 5s	remaining: 2m 13s
331:	learn: 0.0367242	total: 1m 5s	remaining: 

467:	learn: 0.0328369	total: 1m 34s	remaining: 1m 47s
468:	learn: 0.0328149	total: 1m 34s	remaining: 1m 47s
469:	learn: 0.0327785	total: 1m 34s	remaining: 1m 46s
470:	learn: 0.0327727	total: 1m 34s	remaining: 1m 46s
471:	learn: 0.0327572	total: 1m 35s	remaining: 1m 46s
472:	learn: 0.0327353	total: 1m 35s	remaining: 1m 46s
473:	learn: 0.0327277	total: 1m 35s	remaining: 1m 45s
474:	learn: 0.0327100	total: 1m 35s	remaining: 1m 45s
475:	learn: 0.0326893	total: 1m 35s	remaining: 1m 45s
476:	learn: 0.0326580	total: 1m 36s	remaining: 1m 45s
477:	learn: 0.0326509	total: 1m 36s	remaining: 1m 45s
478:	learn: 0.0326421	total: 1m 36s	remaining: 1m 44s
479:	learn: 0.0326291	total: 1m 36s	remaining: 1m 44s
480:	learn: 0.0326128	total: 1m 36s	remaining: 1m 44s
481:	learn: 0.0325622	total: 1m 36s	remaining: 1m 44s
482:	learn: 0.0325408	total: 1m 37s	remaining: 1m 44s
483:	learn: 0.0325168	total: 1m 37s	remaining: 1m 43s
484:	learn: 0.0325095	total: 1m 37s	remaining: 1m 43s
485:	learn: 0.0324889	total:

620:	learn: 0.0300737	total: 2m 5s	remaining: 1m 16s
621:	learn: 0.0300570	total: 2m 5s	remaining: 1m 16s
622:	learn: 0.0300476	total: 2m 6s	remaining: 1m 16s
623:	learn: 0.0300313	total: 2m 6s	remaining: 1m 16s
624:	learn: 0.0300191	total: 2m 6s	remaining: 1m 15s
625:	learn: 0.0300128	total: 2m 6s	remaining: 1m 15s
626:	learn: 0.0300072	total: 2m 6s	remaining: 1m 15s
627:	learn: 0.0300037	total: 2m 6s	remaining: 1m 15s
628:	learn: 0.0299954	total: 2m 7s	remaining: 1m 15s
629:	learn: 0.0299818	total: 2m 7s	remaining: 1m 14s
630:	learn: 0.0299543	total: 2m 7s	remaining: 1m 14s
631:	learn: 0.0299405	total: 2m 7s	remaining: 1m 14s
632:	learn: 0.0299156	total: 2m 8s	remaining: 1m 14s
633:	learn: 0.0299028	total: 2m 8s	remaining: 1m 14s
634:	learn: 0.0298963	total: 2m 8s	remaining: 1m 13s
635:	learn: 0.0298838	total: 2m 8s	remaining: 1m 13s
636:	learn: 0.0298742	total: 2m 8s	remaining: 1m 13s
637:	learn: 0.0298656	total: 2m 9s	remaining: 1m 13s
638:	learn: 0.0298455	total: 2m 9s	remaining: 

776:	learn: 0.0283400	total: 2m 37s	remaining: 45.1s
777:	learn: 0.0283291	total: 2m 37s	remaining: 44.9s
778:	learn: 0.0283229	total: 2m 37s	remaining: 44.7s
779:	learn: 0.0283068	total: 2m 37s	remaining: 44.5s
780:	learn: 0.0283021	total: 2m 37s	remaining: 44.3s
781:	learn: 0.0282980	total: 2m 38s	remaining: 44.1s
782:	learn: 0.0282950	total: 2m 38s	remaining: 43.9s
783:	learn: 0.0282878	total: 2m 38s	remaining: 43.7s
784:	learn: 0.0282827	total: 2m 38s	remaining: 43.5s
785:	learn: 0.0282730	total: 2m 38s	remaining: 43.3s
786:	learn: 0.0282691	total: 2m 39s	remaining: 43.1s
787:	learn: 0.0282670	total: 2m 39s	remaining: 42.9s
788:	learn: 0.0282597	total: 2m 39s	remaining: 42.7s
789:	learn: 0.0282194	total: 2m 39s	remaining: 42.5s
790:	learn: 0.0282006	total: 2m 39s	remaining: 42.3s
791:	learn: 0.0281846	total: 2m 40s	remaining: 42.1s
792:	learn: 0.0281713	total: 2m 40s	remaining: 41.9s
793:	learn: 0.0281655	total: 2m 40s	remaining: 41.7s
794:	learn: 0.0281580	total: 2m 40s	remaining:

933:	learn: 0.0271644	total: 3m 8s	remaining: 13.3s
934:	learn: 0.0271631	total: 3m 8s	remaining: 13.1s
935:	learn: 0.0271568	total: 3m 8s	remaining: 12.9s
936:	learn: 0.0271539	total: 3m 8s	remaining: 12.7s
937:	learn: 0.0271472	total: 3m 8s	remaining: 12.5s
938:	learn: 0.0271379	total: 3m 9s	remaining: 12.3s
939:	learn: 0.0271362	total: 3m 9s	remaining: 12.1s
940:	learn: 0.0271319	total: 3m 9s	remaining: 11.9s
941:	learn: 0.0271005	total: 3m 9s	remaining: 11.7s
942:	learn: 0.0270955	total: 3m 9s	remaining: 11.5s
943:	learn: 0.0270944	total: 3m 10s	remaining: 11.3s
944:	learn: 0.0270846	total: 3m 10s	remaining: 11.1s
945:	learn: 0.0270776	total: 3m 10s	remaining: 10.9s
946:	learn: 0.0270704	total: 3m 10s	remaining: 10.7s
947:	learn: 0.0270654	total: 3m 10s	remaining: 10.5s
948:	learn: 0.0270588	total: 3m 11s	remaining: 10.3s
949:	learn: 0.0270540	total: 3m 11s	remaining: 10.1s
950:	learn: 0.0270489	total: 3m 11s	remaining: 9.86s
951:	learn: 0.0270489	total: 3m 11s	remaining: 9.66s
952

In [27]:
liste_acc

{'MinMaxScaler et HistGradientBoostingClassifier': 0.757553459134271,
 'MinMaxScaler et LGBMClassifier': 0.7626615284508538,
 'MinMaxScaler et CatBoostClassifier': 0.8322406207202742,
 'StandardScaler et HistGradientBoostingClassifier': 0.8723135360900542,
 'StandardScaler et LGBMClassifier': 0.8605986859259712,
 'StandardScaler et CatBoostClassifier': 0.8667021768902441,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.8591152433996792,
 'QuantileTransformer et LGBMClassifier': 0.8481368290740641,
 'QuantileTransformer et CatBoostClassifier': 0.8617732247433045,
 'RobustScaler et HistGradientBoostingClassifier': 0.7766614438840589,
 'RobustScaler et LGBMClassifier': 0.7750129786539315,
 'RobustScaler et CatBoostClassifier': 0.7808304694161837,
 'MaxAbsScaler et HistGradientBoostingClassifier': 0.7186991277874742,
 'MaxAbsScaler et LGBMClassifier': 0.7657910871296385,
 'MaxAbsScaler et CatBoostClassifier': 0.8076516505794,
 'PowerTransformer et HistGradientBoostingClassifier

In [28]:
liste_fscore

{'MinMaxScaler et HistGradientBoostingClassifier': 0.3399736768595436,
 'MinMaxScaler et LGBMClassifier': 0.34411185634092106,
 'MinMaxScaler et CatBoostClassifier': 0.4393127285478134,
 'StandardScaler et HistGradientBoostingClassifier': 0.5573814249954571,
 'StandardScaler et LGBMClassifier': 0.5167221597777448,
 'StandardScaler et CatBoostClassifier': 0.528654464190094,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.5061245570644722,
 'QuantileTransformer et LGBMClassifier': 0.47243309970050756,
 'QuantileTransformer et CatBoostClassifier': 0.5093877881924184,
 'RobustScaler et HistGradientBoostingClassifier': 0.18275373090093333,
 'RobustScaler et LGBMClassifier': 0.208773795534168,
 'RobustScaler et CatBoostClassifier': 0.16918454056321677,
 'MaxAbsScaler et HistGradientBoostingClassifier': 0.31218778335964664,
 'MaxAbsScaler et LGBMClassifier': 0.33507628815567514,
 'MaxAbsScaler et CatBoostClassifier': 0.3709533846316588,
 'PowerTransformer et HistGradientBoostingCl

# Train house 1 Test house 2 - le jour

In [16]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

house2_power_blk1 = house2_power_blk1.between_time('6:00:00', '21:59:59')
house1_power_blk2 = house1_power_blk2.between_time('6:00:00', '21:59:59')

In [17]:
taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_train = house1_power_blk2.iloc[:,-1]
X_train = house1_power_blk2.iloc[:,:-1]

y_test = house2_power_blk1.iloc[:,-1]
X_test = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [18]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "MaxAbsScaler", "PowerTransformer"]

liste_classifier = [HistGradientBoostingClassifier(), LGBMClassifier(), CatBoostClassifier()]
liste_classifier_name = ["HistGradientBoostingClassifier", "LGBMClassifier", "CatBoostClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0
1
2
Learning rate set to 0.341155
0:	learn: 0.5614122	total: 315ms	remaining: 5m 15s
1:	learn: 0.5126467	total: 608ms	remaining: 5m 3s
2:	learn: 0.4838662	total: 859ms	remaining: 4m 45s
3:	learn: 0.4659050	total: 1.15s	remaining: 4m 47s
4:	learn: 0.4588397	total: 1.45s	remaining: 4m 48s
5:	learn: 0.4430167	total: 1.74s	remaining: 4m 48s
6:	learn: 0.4356988	total: 2.03s	remaining: 4m 47s
7:	learn: 0.4242636	total: 2.33s	remaining: 4m 48s
8:	learn: 0.4132378	total: 2.64s	remaining: 4m 50s
9:	learn: 0.4071142	total: 2.97s	remaining: 4m 54s
10:	learn: 0.3995535	total: 3.25s	remaining: 4m 52s
11:	learn: 0.3933603	total: 3.54s	remaining: 4m 51s
12:	learn: 0.3894657	total: 3.83s	remaining: 4m 50s
13:	learn: 0.3846137	total: 4.11s	remaining: 4m 49s
14:	learn: 0.3812898	total: 4.4s	remaining: 4m 48s
15:	learn: 0.3724681	total: 4.7s	remaining: 4m 49s
16:	learn: 0.3666814	total: 5s	remaining: 4m 49s
17:	learn: 0.3635548	total: 5.28s	remaining: 4m 48s
18:	learn: 0.3602399	total: 5.57s	remaining:

157:	learn: 0.1634537	total: 50.3s	remaining: 4m 28s
158:	learn: 0.1629893	total: 50.7s	remaining: 4m 28s
159:	learn: 0.1622927	total: 51s	remaining: 4m 27s
160:	learn: 0.1616806	total: 51.3s	remaining: 4m 27s
161:	learn: 0.1606404	total: 51.7s	remaining: 4m 27s
162:	learn: 0.1599030	total: 52s	remaining: 4m 27s
163:	learn: 0.1593502	total: 52.4s	remaining: 4m 27s
164:	learn: 0.1587403	total: 52.7s	remaining: 4m 26s
165:	learn: 0.1582369	total: 53s	remaining: 4m 26s
166:	learn: 0.1578269	total: 53.4s	remaining: 4m 26s
167:	learn: 0.1573876	total: 53.7s	remaining: 4m 26s
168:	learn: 0.1567065	total: 54.1s	remaining: 4m 25s
169:	learn: 0.1562846	total: 54.4s	remaining: 4m 25s
170:	learn: 0.1561131	total: 54.7s	remaining: 4m 25s
171:	learn: 0.1557111	total: 55.1s	remaining: 4m 25s
172:	learn: 0.1554482	total: 55.4s	remaining: 4m 24s
173:	learn: 0.1545790	total: 55.7s	remaining: 4m 24s
174:	learn: 0.1543637	total: 56s	remaining: 4m 24s
175:	learn: 0.1537808	total: 56.4s	remaining: 4m 23s
1

311:	learn: 0.1190682	total: 1m 51s	remaining: 4m 6s
312:	learn: 0.1189600	total: 1m 51s	remaining: 4m 5s
313:	learn: 0.1188430	total: 1m 52s	remaining: 4m 5s
314:	learn: 0.1186607	total: 1m 52s	remaining: 4m 5s
315:	learn: 0.1184342	total: 1m 53s	remaining: 4m 4s
316:	learn: 0.1183233	total: 1m 53s	remaining: 4m 4s
317:	learn: 0.1180845	total: 1m 53s	remaining: 4m 4s
318:	learn: 0.1180110	total: 1m 54s	remaining: 4m 3s
319:	learn: 0.1178208	total: 1m 54s	remaining: 4m 3s
320:	learn: 0.1177286	total: 1m 54s	remaining: 4m 3s
321:	learn: 0.1176333	total: 1m 55s	remaining: 4m 2s
322:	learn: 0.1175158	total: 1m 55s	remaining: 4m 2s
323:	learn: 0.1174639	total: 1m 56s	remaining: 4m 2s
324:	learn: 0.1172790	total: 1m 56s	remaining: 4m 1s
325:	learn: 0.1171021	total: 1m 56s	remaining: 4m 1s
326:	learn: 0.1169199	total: 1m 57s	remaining: 4m 1s
327:	learn: 0.1168407	total: 1m 57s	remaining: 4m
328:	learn: 0.1166984	total: 1m 57s	remaining: 4m
329:	learn: 0.1164765	total: 1m 58s	remaining: 4m
33

464:	learn: 0.0997074	total: 2m 49s	remaining: 3m 15s
465:	learn: 0.0996334	total: 2m 50s	remaining: 3m 15s
466:	learn: 0.0995845	total: 2m 50s	remaining: 3m 14s
467:	learn: 0.0994496	total: 2m 51s	remaining: 3m 14s
468:	learn: 0.0994020	total: 2m 51s	remaining: 3m 14s
469:	learn: 0.0993347	total: 2m 52s	remaining: 3m 14s
470:	learn: 0.0992364	total: 2m 52s	remaining: 3m 13s
471:	learn: 0.0988718	total: 2m 52s	remaining: 3m 13s
472:	learn: 0.0987319	total: 2m 53s	remaining: 3m 13s
473:	learn: 0.0986658	total: 2m 53s	remaining: 3m 12s
474:	learn: 0.0985641	total: 2m 54s	remaining: 3m 12s
475:	learn: 0.0984895	total: 2m 54s	remaining: 3m 11s
476:	learn: 0.0983789	total: 2m 54s	remaining: 3m 11s
477:	learn: 0.0983247	total: 2m 55s	remaining: 3m 11s
478:	learn: 0.0982473	total: 2m 55s	remaining: 3m 11s
479:	learn: 0.0981836	total: 2m 56s	remaining: 3m 10s
480:	learn: 0.0981433	total: 2m 56s	remaining: 3m 10s
481:	learn: 0.0980888	total: 2m 57s	remaining: 3m 10s
482:	learn: 0.0980492	total:

618:	learn: 0.0884889	total: 3m 51s	remaining: 2m 22s
619:	learn: 0.0884278	total: 3m 52s	remaining: 2m 22s
620:	learn: 0.0883796	total: 3m 52s	remaining: 2m 21s
621:	learn: 0.0882597	total: 3m 52s	remaining: 2m 21s
622:	learn: 0.0882006	total: 3m 53s	remaining: 2m 21s
623:	learn: 0.0881457	total: 3m 53s	remaining: 2m 20s
624:	learn: 0.0881037	total: 3m 53s	remaining: 2m 20s
625:	learn: 0.0880636	total: 3m 54s	remaining: 2m 20s
626:	learn: 0.0880104	total: 3m 54s	remaining: 2m 19s
627:	learn: 0.0879710	total: 3m 55s	remaining: 2m 19s
628:	learn: 0.0879416	total: 3m 55s	remaining: 2m 18s
629:	learn: 0.0878953	total: 3m 55s	remaining: 2m 18s
630:	learn: 0.0878815	total: 3m 56s	remaining: 2m 18s
631:	learn: 0.0878443	total: 3m 56s	remaining: 2m 17s
632:	learn: 0.0878028	total: 3m 56s	remaining: 2m 17s
633:	learn: 0.0877727	total: 3m 57s	remaining: 2m 16s
634:	learn: 0.0877267	total: 3m 57s	remaining: 2m 16s
635:	learn: 0.0876631	total: 3m 58s	remaining: 2m 16s
636:	learn: 0.0875858	total:

...

258:	learn: 0.1278529	total: 1m 21s	remaining: 3m 53s
259:	learn: 0.1275855	total: 1m 22s	remaining: 3m 53s
260:	learn: 0.1274416	total: 1m 22s	remaining: 3m 53s
261:	learn: 0.1273403	total: 1m 22s	remaining: 3m 53s
262:	learn: 0.1272238	total: 1m 23s	remaining: 3m 53s
263:	learn: 0.1268138	total: 1m 23s	remaining: 3m 53s
264:	learn: 0.1262250	total: 1m 23s	remaining: 3m 52s
265:	learn: 0.1260979	total: 1m 24s	remaining: 3m 52s
266:	learn: 0.1257931	total: 1m 24s	remaining: 3m 52s
267:	learn: 0.1254449	total: 1m 25s	remaining: 3m 52s
268:	learn: 0.1253213	total: 1m 25s	remaining: 3m 52s
269:	learn: 0.1250067	total: 1m 25s	remaining: 3m 52s
270:	learn: 0.1247489	total: 1m 26s	remaining: 3m 51s
271:	learn: 0.1245688	total: 1m 26s	remaining: 3m 51s
272:	learn: 0.1245054	total: 1m 26s	remaining: 3m 51s
273:	learn: 0.1242298	total: 1m 27s	remaining: 3m 51s
274:	learn: 0.1241669	total: 1m 27s	remaining: 3m 50s
275:	learn: 0.1239516	total: 1m 27s	remaining: 3m 50s
276:	learn: 0.1238889	total:

411:	learn: 0.1046798	total: 2m 18s	remaining: 3m 17s
412:	learn: 0.1046193	total: 2m 18s	remaining: 3m 17s
413:	learn: 0.1045688	total: 2m 18s	remaining: 3m 16s
414:	learn: 0.1044819	total: 2m 19s	remaining: 3m 16s
415:	learn: 0.1043186	total: 2m 19s	remaining: 3m 16s
416:	learn: 0.1041795	total: 2m 20s	remaining: 3m 15s
417:	learn: 0.1041196	total: 2m 20s	remaining: 3m 15s
418:	learn: 0.1040409	total: 2m 20s	remaining: 3m 15s
419:	learn: 0.1039724	total: 2m 21s	remaining: 3m 14s
420:	learn: 0.1039529	total: 2m 21s	remaining: 3m 14s
421:	learn: 0.1038877	total: 2m 21s	remaining: 3m 14s
422:	learn: 0.1036068	total: 2m 22s	remaining: 3m 14s
423:	learn: 0.1035317	total: 2m 22s	remaining: 3m 13s
424:	learn: 0.1034472	total: 2m 23s	remaining: 3m 13s
425:	learn: 0.1033411	total: 2m 23s	remaining: 3m 13s
426:	learn: 0.1032644	total: 2m 23s	remaining: 3m 13s
427:	learn: 0.1031844	total: 2m 24s	remaining: 3m 12s
428:	learn: 0.1029887	total: 2m 24s	remaining: 3m 12s
429:	learn: 0.1029130	total:

565:	learn: 0.0920260	total: 3m 16s	remaining: 2m 30s
566:	learn: 0.0919757	total: 3m 16s	remaining: 2m 30s
567:	learn: 0.0918683	total: 3m 17s	remaining: 2m 29s
568:	learn: 0.0918015	total: 3m 17s	remaining: 2m 29s
569:	learn: 0.0917260	total: 3m 17s	remaining: 2m 29s
570:	learn: 0.0916659	total: 3m 18s	remaining: 2m 28s
571:	learn: 0.0916293	total: 3m 18s	remaining: 2m 28s
572:	learn: 0.0915496	total: 3m 18s	remaining: 2m 28s
573:	learn: 0.0915190	total: 3m 19s	remaining: 2m 27s
574:	learn: 0.0914423	total: 3m 19s	remaining: 2m 27s
575:	learn: 0.0913525	total: 3m 19s	remaining: 2m 27s
576:	learn: 0.0912772	total: 3m 20s	remaining: 2m 26s
577:	learn: 0.0912447	total: 3m 20s	remaining: 2m 26s
578:	learn: 0.0912028	total: 3m 21s	remaining: 2m 26s
579:	learn: 0.0911371	total: 3m 21s	remaining: 2m 25s
580:	learn: 0.0910926	total: 3m 21s	remaining: 2m 25s
581:	learn: 0.0910379	total: 3m 22s	remaining: 2m 25s
582:	learn: 0.0910108	total: 3m 22s	remaining: 2m 24s
583:	learn: 0.0909629	total:

719:	learn: 0.0837650	total: 4m 13s	remaining: 1m 38s
720:	learn: 0.0837407	total: 4m 14s	remaining: 1m 38s
721:	learn: 0.0836581	total: 4m 14s	remaining: 1m 37s
722:	learn: 0.0836106	total: 4m 14s	remaining: 1m 37s
723:	learn: 0.0835504	total: 4m 15s	remaining: 1m 37s
724:	learn: 0.0835197	total: 4m 15s	remaining: 1m 36s
725:	learn: 0.0834904	total: 4m 15s	remaining: 1m 36s
726:	learn: 0.0834546	total: 4m 16s	remaining: 1m 36s
727:	learn: 0.0834288	total: 4m 16s	remaining: 1m 35s
728:	learn: 0.0834054	total: 4m 16s	remaining: 1m 35s
729:	learn: 0.0833734	total: 4m 17s	remaining: 1m 35s
730:	learn: 0.0833387	total: 4m 17s	remaining: 1m 34s
731:	learn: 0.0832578	total: 4m 18s	remaining: 1m 34s
732:	learn: 0.0832044	total: 4m 18s	remaining: 1m 34s
733:	learn: 0.0831763	total: 4m 18s	remaining: 1m 33s
734:	learn: 0.0831332	total: 4m 19s	remaining: 1m 33s
735:	learn: 0.0831004	total: 4m 19s	remaining: 1m 33s
736:	learn: 0.0830292	total: 4m 20s	remaining: 1m 32s
737:	learn: 0.0829947	total:

873:	learn: 0.0779402	total: 5m 15s	remaining: 45.4s
874:	learn: 0.0779090	total: 5m 15s	remaining: 45.1s
875:	learn: 0.0778829	total: 5m 15s	remaining: 44.7s
876:	learn: 0.0778031	total: 5m 16s	remaining: 44.4s
877:	learn: 0.0777260	total: 5m 16s	remaining: 44s
878:	learn: 0.0776616	total: 5m 17s	remaining: 43.7s
879:	learn: 0.0776252	total: 5m 17s	remaining: 43.3s
880:	learn: 0.0776150	total: 5m 18s	remaining: 43s
881:	learn: 0.0775274	total: 5m 18s	remaining: 42.6s
882:	learn: 0.0775078	total: 5m 18s	remaining: 42.2s
883:	learn: 0.0774371	total: 5m 19s	remaining: 41.9s
884:	learn: 0.0774134	total: 5m 19s	remaining: 41.5s
885:	learn: 0.0773945	total: 5m 19s	remaining: 41.2s
886:	learn: 0.0773748	total: 5m 20s	remaining: 40.8s
887:	learn: 0.0773605	total: 5m 20s	remaining: 40.4s
888:	learn: 0.0773425	total: 5m 21s	remaining: 40.1s
889:	learn: 0.0773007	total: 5m 21s	remaining: 39.7s
890:	learn: 0.0772621	total: 5m 21s	remaining: 39.4s
891:	learn: 0.0772305	total: 5m 22s	remaining: 39s

In [19]:
liste_acc

{'MinMaxScaler et HistGradientBoostingClassifier': 0.6958294442436962,
 'MinMaxScaler et LGBMClassifier': 0.6903904077099903,
 'MinMaxScaler et CatBoostClassifier': 0.6836984271403332,
 'StandardScaler et HistGradientBoostingClassifier': 0.6585653937916593,
 'StandardScaler et LGBMClassifier': 0.6673221719893738,
 'StandardScaler et CatBoostClassifier': 0.6364220061464291,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.7051367762909325,
 'QuantileTransformer et LGBMClassifier': 0.6927138567724302,
 'QuantileTransformer et CatBoostClassifier': 0.6451911431157522,
 'RobustScaler et HistGradientBoostingClassifier': 0.726398865817874,
 'RobustScaler et LGBMClassifier': 0.701427967782448,
 'RobustScaler et CatBoostClassifier': 0.6512384077664874,
 'MaxAbsScaler et HistGradientBoostingClassifier': 0.7085889931603027,
 'MaxAbsScaler et LGBMClassifier': 0.6978030223670225,
 'MaxAbsScaler et CatBoostClassifier': 0.6500663842589268,
 'PowerTransformer et HistGradientBoostingClassifi

In [20]:
liste_fscore

{'MinMaxScaler et HistGradientBoostingClassifier': 0.7264064425516851,
 'MinMaxScaler et LGBMClassifier': 0.7287121903474616,
 'MinMaxScaler et CatBoostClassifier': 0.7232538961833508,
 'StandardScaler et HistGradientBoostingClassifier': 0.6885664780812822,
 'StandardScaler et LGBMClassifier': 0.6944826203109407,
 'StandardScaler et CatBoostClassifier': 0.6743607520832409,
 'QuantileTransformer et HistGradientBoostingClassifier': 0.7388115279565726,
 'QuantileTransformer et LGBMClassifier': 0.7300358673497457,
 'QuantileTransformer et CatBoostClassifier': 0.6872923410374775,
 'RobustScaler et HistGradientBoostingClassifier': 0.7484936920523264,
 'RobustScaler et LGBMClassifier': 0.7249677188340262,
 'RobustScaler et CatBoostClassifier': 0.6886522421466809,
 'MaxAbsScaler et HistGradientBoostingClassifier': 0.7668899769291254,
 'MaxAbsScaler et LGBMClassifier': 0.7384326089577165,
 'MaxAbsScaler et CatBoostClassifier': 0.6982543748755928,
 'PowerTransformer et HistGradientBoostingClassi

# voting Train house 1 Test house 2

In [8]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_train = house1_power_blk2.iloc[:,-1]
X_train = house1_power_blk2.iloc[:,:-1]

y_test = house2_power_blk1.iloc[:,-1]
X_test = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [9]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), Normalizer(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "Normalizer", "MaxAbsScaler", "PowerTransformer"]

clf1 = XGBClassifier()
clf2 = HistGradientBoostingClassifier()
clf3 = LGBMClassifier()
clf4 = CatBoostClassifier()

liste_classifier = [VotingClassifier(estimators=[('XGB', clf1), ('HGB', clf2), ('LGBM', clf3), ('CBC', clf4)], voting='soft', weights=[0.1, 0.3, 0.3, 0.3])]
liste_classifier_name = ["VotingClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore


0


C:\Users\julie\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[12:10:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Learning rate set to 0.405527
0:	learn: 0.4921287	total: 565ms	remaining: 9m 24s
1:	learn: 0.4355427	total: 1s	remaining: 8m 21s
2:	learn: 0.4129380	total: 1.45s	remaining: 8m 3s
3:	learn: 0.4017151	total: 1.93s	remaining: 7m 59s
4:	learn: 0.3906542	total: 2.41s	remaining: 7m 59s
5:	learn: 0.3811948	total: 2.92s	remaining: 8m 4s
6:	learn: 0.3749936	total: 3.46s	remaining: 8m 11s
7:	learn: 0.3687734	total: 3.99s	remaining: 8m 15s
8:	learn: 0.3605618	total: 4.5s	remaining: 8m 15s
9:	learn: 0.3537852	total: 5.01s	remaining: 8m 15s
10:	learn: 0.3488726	total: 5.47s	remaining: 8m 11s
11:	learn: 0.3413029	total: 5.91s	remaining: 8m 6s
12:	learn: 0.3353873	total: 6.44s	remaining: 8m 9s
13

151:	learn: 0.1490679	total: 1m 19s	remaining: 7m 23s
152:	learn: 0.1488877	total: 1m 20s	remaining: 7m 23s
153:	learn: 0.1484516	total: 1m 20s	remaining: 7m 22s
154:	learn: 0.1479587	total: 1m 21s	remaining: 7m 22s
155:	learn: 0.1475607	total: 1m 21s	remaining: 7m 21s
156:	learn: 0.1473809	total: 1m 22s	remaining: 7m 21s
157:	learn: 0.1469247	total: 1m 22s	remaining: 7m 20s
158:	learn: 0.1466019	total: 1m 23s	remaining: 7m 20s
159:	learn: 0.1460903	total: 1m 23s	remaining: 7m 19s
160:	learn: 0.1458642	total: 1m 24s	remaining: 7m 19s
161:	learn: 0.1453578	total: 1m 24s	remaining: 7m 18s
162:	learn: 0.1449379	total: 1m 25s	remaining: 7m 18s
163:	learn: 0.1448605	total: 1m 25s	remaining: 7m 17s
164:	learn: 0.1443168	total: 1m 26s	remaining: 7m 17s
165:	learn: 0.1440569	total: 1m 26s	remaining: 7m 17s
166:	learn: 0.1436461	total: 1m 27s	remaining: 7m 16s
167:	learn: 0.1433895	total: 1m 28s	remaining: 7m 16s
168:	learn: 0.1428949	total: 1m 28s	remaining: 7m 15s
169:	learn: 0.1426612	total:

305:	learn: 0.1074049	total: 2m 37s	remaining: 5m 57s
306:	learn: 0.1070879	total: 2m 38s	remaining: 5m 56s
307:	learn: 0.1070052	total: 2m 38s	remaining: 5m 56s
308:	learn: 0.1068122	total: 2m 39s	remaining: 5m 55s
309:	learn: 0.1066777	total: 2m 39s	remaining: 5m 55s
310:	learn: 0.1065266	total: 2m 40s	remaining: 5m 54s
311:	learn: 0.1064102	total: 2m 40s	remaining: 5m 54s
312:	learn: 0.1062634	total: 2m 41s	remaining: 5m 53s
313:	learn: 0.1062029	total: 2m 41s	remaining: 5m 53s
314:	learn: 0.1059576	total: 2m 42s	remaining: 5m 52s
315:	learn: 0.1057494	total: 2m 42s	remaining: 5m 52s
316:	learn: 0.1055670	total: 2m 43s	remaining: 5m 51s
317:	learn: 0.1054619	total: 2m 43s	remaining: 5m 51s
318:	learn: 0.1053778	total: 2m 44s	remaining: 5m 50s
319:	learn: 0.1051995	total: 2m 44s	remaining: 5m 50s
320:	learn: 0.1050394	total: 2m 45s	remaining: 5m 49s
321:	learn: 0.1048500	total: 2m 45s	remaining: 5m 49s
322:	learn: 0.1047339	total: 2m 46s	remaining: 5m 48s
323:	learn: 0.1046333	total:

...

305:	learn: 0.1087095	total: 2m 31s	remaining: 5m 43s
306:	learn: 0.1084695	total: 2m 31s	remaining: 5m 42s
307:	learn: 0.1083590	total: 2m 32s	remaining: 5m 42s
308:	learn: 0.1082071	total: 2m 32s	remaining: 5m 41s
309:	learn: 0.1080809	total: 2m 33s	remaining: 5m 41s
310:	learn: 0.1077572	total: 2m 34s	remaining: 5m 41s
311:	learn: 0.1075243	total: 2m 34s	remaining: 5m 41s
312:	learn: 0.1073907	total: 2m 35s	remaining: 5m 40s
313:	learn: 0.1072774	total: 2m 35s	remaining: 5m 40s
314:	learn: 0.1069829	total: 2m 36s	remaining: 5m 40s
315:	learn: 0.1066674	total: 2m 37s	remaining: 5m 40s
316:	learn: 0.1065263	total: 2m 37s	remaining: 5m 39s
317:	learn: 0.1064334	total: 2m 38s	remaining: 5m 39s
318:	learn: 0.1063264	total: 2m 38s	remaining: 5m 39s
319:	learn: 0.1061354	total: 2m 39s	remaining: 5m 38s
320:	learn: 0.1059166	total: 2m 40s	remaining: 5m 38s
321:	learn: 0.1058135	total: 2m 40s	remaining: 5m 38s
322:	learn: 0.1057407	total: 2m 41s	remaining: 5m 37s
323:	learn: 0.1056280	total:

458:	learn: 0.0902383	total: 3m 51s	remaining: 4m 33s
459:	learn: 0.0901379	total: 3m 52s	remaining: 4m 32s
460:	learn: 0.0900810	total: 3m 52s	remaining: 4m 32s
461:	learn: 0.0898972	total: 3m 53s	remaining: 4m 31s
462:	learn: 0.0898355	total: 3m 53s	remaining: 4m 31s
463:	learn: 0.0898113	total: 3m 54s	remaining: 4m 30s
464:	learn: 0.0897088	total: 3m 54s	remaining: 4m 29s
465:	learn: 0.0896002	total: 3m 55s	remaining: 4m 29s
466:	learn: 0.0895590	total: 3m 55s	remaining: 4m 28s
467:	learn: 0.0895136	total: 3m 56s	remaining: 4m 28s
468:	learn: 0.0893726	total: 3m 56s	remaining: 4m 27s
469:	learn: 0.0893513	total: 3m 56s	remaining: 4m 27s
470:	learn: 0.0892730	total: 3m 57s	remaining: 4m 26s
471:	learn: 0.0892035	total: 3m 57s	remaining: 4m 26s
472:	learn: 0.0891632	total: 3m 58s	remaining: 4m 25s
473:	learn: 0.0890436	total: 3m 58s	remaining: 4m 25s
474:	learn: 0.0889964	total: 3m 59s	remaining: 4m 24s
475:	learn: 0.0888345	total: 3m 59s	remaining: 4m 24s
476:	learn: 0.0887669	total:

612:	learn: 0.0795175	total: 5m 10s	remaining: 3m 16s
613:	learn: 0.0794573	total: 5m 11s	remaining: 3m 15s
614:	learn: 0.0794088	total: 5m 11s	remaining: 3m 15s
615:	learn: 0.0793815	total: 5m 12s	remaining: 3m 14s
616:	learn: 0.0792994	total: 5m 12s	remaining: 3m 14s
617:	learn: 0.0792724	total: 5m 13s	remaining: 3m 13s
618:	learn: 0.0792430	total: 5m 13s	remaining: 3m 13s
619:	learn: 0.0791936	total: 5m 14s	remaining: 3m 12s
620:	learn: 0.0791439	total: 5m 14s	remaining: 3m 12s
621:	learn: 0.0791034	total: 5m 15s	remaining: 3m 11s
622:	learn: 0.0790433	total: 5m 15s	remaining: 3m 11s
623:	learn: 0.0790063	total: 5m 16s	remaining: 3m 10s
624:	learn: 0.0789329	total: 5m 17s	remaining: 3m 10s
625:	learn: 0.0788981	total: 5m 17s	remaining: 3m 9s
626:	learn: 0.0787574	total: 5m 18s	remaining: 3m 9s
627:	learn: 0.0787146	total: 5m 18s	remaining: 3m 8s
628:	learn: 0.0786882	total: 5m 19s	remaining: 3m 8s
629:	learn: 0.0786310	total: 5m 19s	remaining: 3m 7s
630:	learn: 0.0786158	total: 5m 2

766:	learn: 0.0726849	total: 6m 32s	remaining: 1m 59s
767:	learn: 0.0726590	total: 6m 32s	remaining: 1m 58s
768:	learn: 0.0725946	total: 6m 33s	remaining: 1m 58s
769:	learn: 0.0725381	total: 6m 34s	remaining: 1m 57s
770:	learn: 0.0725153	total: 6m 34s	remaining: 1m 57s
771:	learn: 0.0724840	total: 6m 35s	remaining: 1m 56s
772:	learn: 0.0724588	total: 6m 35s	remaining: 1m 56s
773:	learn: 0.0724408	total: 6m 36s	remaining: 1m 55s
774:	learn: 0.0724152	total: 6m 36s	remaining: 1m 55s
775:	learn: 0.0723898	total: 6m 37s	remaining: 1m 54s
776:	learn: 0.0723514	total: 6m 37s	remaining: 1m 54s
777:	learn: 0.0722523	total: 6m 38s	remaining: 1m 53s
778:	learn: 0.0722015	total: 6m 38s	remaining: 1m 53s
779:	learn: 0.0721465	total: 6m 39s	remaining: 1m 52s
780:	learn: 0.0721225	total: 6m 39s	remaining: 1m 52s
781:	learn: 0.0720850	total: 6m 40s	remaining: 1m 51s
782:	learn: 0.0720274	total: 6m 40s	remaining: 1m 51s
783:	learn: 0.0719962	total: 6m 41s	remaining: 1m 50s
784:	learn: 0.0719618	total:

920:	learn: 0.0676643	total: 7m 48s	remaining: 40.2s
921:	learn: 0.0676524	total: 7m 48s	remaining: 39.7s
922:	learn: 0.0676333	total: 7m 49s	remaining: 39.2s
923:	learn: 0.0675767	total: 7m 50s	remaining: 38.7s
924:	learn: 0.0675424	total: 7m 50s	remaining: 38.1s
925:	learn: 0.0675199	total: 7m 51s	remaining: 37.6s
926:	learn: 0.0675048	total: 7m 51s	remaining: 37.1s
927:	learn: 0.0674912	total: 7m 52s	remaining: 36.6s
928:	learn: 0.0674580	total: 7m 52s	remaining: 36.1s
929:	learn: 0.0674364	total: 7m 53s	remaining: 35.6s
930:	learn: 0.0673752	total: 7m 53s	remaining: 35.1s
931:	learn: 0.0673507	total: 7m 54s	remaining: 34.6s
932:	learn: 0.0673274	total: 7m 54s	remaining: 34.1s
933:	learn: 0.0672619	total: 7m 55s	remaining: 33.6s
934:	learn: 0.0672533	total: 7m 55s	remaining: 33.1s
935:	learn: 0.0672173	total: 7m 56s	remaining: 32.6s
936:	learn: 0.0671895	total: 7m 56s	remaining: 32.1s
937:	learn: 0.0671793	total: 7m 57s	remaining: 31.6s
938:	learn: 0.0671579	total: 7m 57s	remaining:

In [10]:
liste_acc

{'MinMaxScaler et VotingClassifier': 0.7099058416150578,
 'StandardScaler et VotingClassifier': 0.7270804549211243,
 'QuantileTransformer et VotingClassifier': 0.7392258515264668,
 'RobustScaler et VotingClassifier': 0.689652536113128,
 'Normalizer et VotingClassifier': 0.5925677763158101,
 'MaxAbsScaler et VotingClassifier': 0.737601329257946,
 'PowerTransformer et VotingClassifier': 0.7479794918521004}

In [11]:
liste_fscore

{'MinMaxScaler et VotingClassifier': 0.6640874511525008,
 'StandardScaler et VotingClassifier': 0.6761678789451608,
 'QuantileTransformer et VotingClassifier': 0.6928089446519758,
 'RobustScaler et VotingClassifier': 0.6435789510041812,
 'Normalizer et VotingClassifier': 0.40542073407833706,
 'MaxAbsScaler et VotingClassifier': 0.6979952514122514,
 'PowerTransformer et VotingClassifier': 0.7005731769189857}

# voting Train house 2 Test house 1

In [12]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_test = house1_power_blk2.iloc[:,-1]
X_test = house1_power_blk2.iloc[:,:-1]

y_train = house2_power_blk1.iloc[:,-1]
X_train = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [13]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), Normalizer(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "Normalizer", "MaxAbsScaler", "PowerTransformer"]

clf1 = XGBClassifier()
clf2 = HistGradientBoostingClassifier()
clf3 = LGBMClassifier()
clf4 = CatBoostClassifier()

liste_classifier = [VotingClassifier(estimators=[('XGB', clf1), ('HGB', clf2), ('LGBM', clf3), ('CBC', clf4)], voting='soft', weights=[0.1, 0.3, 0.3, 0.3])]
liste_classifier_name = ["VotingClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0


C:\Users\julie\anaconda3\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[14:16:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.1/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Learning rate set to 0.394557
0:	learn: 0.4677154	total: 387ms	remaining: 6m 26s
1:	learn: 0.4092024	total: 783ms	remaining: 6m 30s
2:	learn: 0.3828489	total: 1.21s	remaining: 6m 42s
3:	learn: 0.3697802	total: 1.69s	remaining: 7m 1s
4:	learn: 0.3582998	total: 2.11s	remaining: 7m
5:	learn: 0.3496475	total: 2.57s	remaining: 7m 5s
6:	learn: 0.3427465	total: 3s	remaining: 7m 6s
7:	learn: 0.3399817	total: 3.5s	remaining: 7m 14s
8:	learn: 0.3349435	total: 4.04s	remaining: 7m 24s
9:	learn: 0.3294625	total: 4.55s	remaining: 7m 30s
10:	learn: 0.3236186	total: 5.04s	remaining: 7m 33s
11:	learn: 0.3193842	total: 5.48s	remaining: 7m 30s
12:	learn: 0.3162028	total: 5.94s	remaining: 7m 31s
13:	l

152:	learn: 0.1487398	total: 1m 15s	remaining: 6m 57s
153:	learn: 0.1481671	total: 1m 15s	remaining: 6m 56s
154:	learn: 0.1477241	total: 1m 16s	remaining: 6m 56s
155:	learn: 0.1471780	total: 1m 16s	remaining: 6m 56s
156:	learn: 0.1461516	total: 1m 17s	remaining: 6m 55s
157:	learn: 0.1458530	total: 1m 17s	remaining: 6m 54s
158:	learn: 0.1454152	total: 1m 18s	remaining: 6m 54s
159:	learn: 0.1448235	total: 1m 18s	remaining: 6m 54s
160:	learn: 0.1444256	total: 1m 19s	remaining: 6m 53s
161:	learn: 0.1440793	total: 1m 19s	remaining: 6m 53s
162:	learn: 0.1434760	total: 1m 20s	remaining: 6m 53s
163:	learn: 0.1429940	total: 1m 20s	remaining: 6m 52s
164:	learn: 0.1426709	total: 1m 21s	remaining: 6m 52s
165:	learn: 0.1424030	total: 1m 22s	remaining: 6m 52s
166:	learn: 0.1418766	total: 1m 22s	remaining: 6m 52s
167:	learn: 0.1413711	total: 1m 23s	remaining: 6m 51s
168:	learn: 0.1411074	total: 1m 23s	remaining: 6m 51s
169:	learn: 0.1405441	total: 1m 24s	remaining: 6m 51s
170:	learn: 0.1401331	total:

305:	learn: 0.1050206	total: 2m 33s	remaining: 5m 47s
306:	learn: 0.1048027	total: 2m 33s	remaining: 5m 47s
307:	learn: 0.1046776	total: 2m 34s	remaining: 5m 46s
308:	learn: 0.1046157	total: 2m 34s	remaining: 5m 46s
309:	learn: 0.1044558	total: 2m 35s	remaining: 5m 45s
310:	learn: 0.1042274	total: 2m 35s	remaining: 5m 45s
311:	learn: 0.1040761	total: 2m 36s	remaining: 5m 44s
312:	learn: 0.1038599	total: 2m 37s	remaining: 5m 44s
313:	learn: 0.1036693	total: 2m 37s	remaining: 5m 44s
314:	learn: 0.1034750	total: 2m 38s	remaining: 5m 44s
315:	learn: 0.1033670	total: 2m 39s	remaining: 5m 44s
316:	learn: 0.1031670	total: 2m 39s	remaining: 5m 44s
317:	learn: 0.1030139	total: 2m 40s	remaining: 5m 43s
318:	learn: 0.1029025	total: 2m 40s	remaining: 5m 43s
319:	learn: 0.1027854	total: 2m 41s	remaining: 5m 42s
320:	learn: 0.1025756	total: 2m 41s	remaining: 5m 42s
321:	learn: 0.1024852	total: 2m 42s	remaining: 5m 42s
322:	learn: 0.1023299	total: 2m 43s	remaining: 5m 41s
323:	learn: 0.1022089	total:

...

307:	learn: 0.1050970	total: 2m 44s	remaining: 6m 9s
308:	learn: 0.1049467	total: 2m 45s	remaining: 6m 10s
309:	learn: 0.1047522	total: 2m 46s	remaining: 6m 10s
310:	learn: 0.1046362	total: 2m 47s	remaining: 6m 10s
311:	learn: 0.1043939	total: 2m 48s	remaining: 6m 10s
312:	learn: 0.1042770	total: 2m 48s	remaining: 6m 10s
313:	learn: 0.1040752	total: 2m 49s	remaining: 6m 10s
314:	learn: 0.1039230	total: 2m 50s	remaining: 6m 10s
315:	learn: 0.1037755	total: 2m 51s	remaining: 6m 10s
316:	learn: 0.1036488	total: 2m 51s	remaining: 6m 10s
317:	learn: 0.1034933	total: 2m 53s	remaining: 6m 11s
318:	learn: 0.1032781	total: 2m 54s	remaining: 6m 11s
319:	learn: 0.1031274	total: 2m 54s	remaining: 6m 11s
320:	learn: 0.1029907	total: 2m 55s	remaining: 6m 11s
321:	learn: 0.1028860	total: 2m 56s	remaining: 6m 11s
322:	learn: 0.1027627	total: 2m 56s	remaining: 6m 10s
323:	learn: 0.1025422	total: 2m 57s	remaining: 6m 10s
324:	learn: 0.1023511	total: 2m 58s	remaining: 6m 9s
325:	learn: 0.1021572	total: 2

461:	learn: 0.0856812	total: 4m 29s	remaining: 5m 13s
462:	learn: 0.0856305	total: 4m 29s	remaining: 5m 13s
463:	learn: 0.0855642	total: 4m 30s	remaining: 5m 12s
464:	learn: 0.0854722	total: 4m 31s	remaining: 5m 11s
465:	learn: 0.0853855	total: 4m 31s	remaining: 5m 11s
466:	learn: 0.0853200	total: 4m 32s	remaining: 5m 10s
467:	learn: 0.0852245	total: 4m 32s	remaining: 5m 10s
468:	learn: 0.0851482	total: 4m 33s	remaining: 5m 9s
469:	learn: 0.0850899	total: 4m 34s	remaining: 5m 9s
470:	learn: 0.0850090	total: 4m 34s	remaining: 5m 8s
471:	learn: 0.0848840	total: 4m 35s	remaining: 5m 7s
472:	learn: 0.0848362	total: 4m 35s	remaining: 5m 7s
473:	learn: 0.0846643	total: 4m 36s	remaining: 5m 6s
474:	learn: 0.0845398	total: 4m 37s	remaining: 5m 6s
475:	learn: 0.0845179	total: 4m 37s	remaining: 5m 5s
476:	learn: 0.0844547	total: 4m 38s	remaining: 5m 5s
477:	learn: 0.0843461	total: 4m 39s	remaining: 5m 4s
478:	learn: 0.0842508	total: 4m 39s	remaining: 5m 4s
479:	learn: 0.0840731	total: 4m 40s	rem

615:	learn: 0.0757726	total: 6m 6s	remaining: 3m 48s
616:	learn: 0.0757277	total: 6m 7s	remaining: 3m 47s
617:	learn: 0.0756842	total: 6m 7s	remaining: 3m 47s
618:	learn: 0.0756429	total: 6m 8s	remaining: 3m 46s
619:	learn: 0.0756021	total: 6m 9s	remaining: 3m 46s
620:	learn: 0.0755540	total: 6m 9s	remaining: 3m 45s
621:	learn: 0.0755000	total: 6m 10s	remaining: 3m 45s
622:	learn: 0.0754613	total: 6m 10s	remaining: 3m 44s
623:	learn: 0.0754187	total: 6m 11s	remaining: 3m 43s
624:	learn: 0.0753864	total: 6m 12s	remaining: 3m 43s
625:	learn: 0.0753608	total: 6m 12s	remaining: 3m 42s
626:	learn: 0.0753145	total: 6m 13s	remaining: 3m 42s
627:	learn: 0.0752345	total: 6m 13s	remaining: 3m 41s
628:	learn: 0.0752014	total: 6m 14s	remaining: 3m 40s
629:	learn: 0.0751324	total: 6m 15s	remaining: 3m 40s
630:	learn: 0.0751047	total: 6m 15s	remaining: 3m 39s
631:	learn: 0.0750843	total: 6m 16s	remaining: 3m 39s
632:	learn: 0.0750467	total: 6m 17s	remaining: 3m 38s
633:	learn: 0.0749993	total: 6m 17

768:	learn: 0.0700119	total: 7m 43s	remaining: 2m 19s
769:	learn: 0.0699529	total: 7m 44s	remaining: 2m 18s
770:	learn: 0.0699361	total: 7m 44s	remaining: 2m 18s
771:	learn: 0.0699195	total: 7m 45s	remaining: 2m 17s
772:	learn: 0.0698948	total: 7m 46s	remaining: 2m 16s
773:	learn: 0.0698364	total: 7m 46s	remaining: 2m 16s
774:	learn: 0.0698211	total: 7m 47s	remaining: 2m 15s
775:	learn: 0.0698054	total: 7m 48s	remaining: 2m 15s
776:	learn: 0.0697285	total: 7m 48s	remaining: 2m 14s
777:	learn: 0.0697123	total: 7m 49s	remaining: 2m 13s
778:	learn: 0.0696721	total: 7m 50s	remaining: 2m 13s
779:	learn: 0.0696380	total: 7m 50s	remaining: 2m 12s
780:	learn: 0.0696034	total: 7m 51s	remaining: 2m 12s
781:	learn: 0.0695737	total: 7m 52s	remaining: 2m 11s
782:	learn: 0.0695518	total: 7m 52s	remaining: 2m 11s
783:	learn: 0.0695259	total: 7m 53s	remaining: 2m 10s
784:	learn: 0.0695004	total: 7m 54s	remaining: 2m 9s
785:	learn: 0.0693823	total: 7m 54s	remaining: 2m 9s
786:	learn: 0.0693129	total: 7

922:	learn: 0.0653358	total: 9m 17s	remaining: 46.5s
923:	learn: 0.0653304	total: 9m 18s	remaining: 46s
924:	learn: 0.0653149	total: 9m 19s	remaining: 45.3s
925:	learn: 0.0652899	total: 9m 19s	remaining: 44.7s
926:	learn: 0.0652519	total: 9m 20s	remaining: 44.1s
927:	learn: 0.0652385	total: 9m 21s	remaining: 43.5s
928:	learn: 0.0651797	total: 9m 21s	remaining: 42.9s
929:	learn: 0.0651624	total: 9m 22s	remaining: 42.3s
930:	learn: 0.0651388	total: 9m 22s	remaining: 41.7s
931:	learn: 0.0651225	total: 9m 23s	remaining: 41.1s
932:	learn: 0.0651153	total: 9m 24s	remaining: 40.5s
933:	learn: 0.0650852	total: 9m 24s	remaining: 39.9s
934:	learn: 0.0650663	total: 9m 25s	remaining: 39.3s
935:	learn: 0.0650284	total: 9m 26s	remaining: 38.7s
936:	learn: 0.0650000	total: 9m 26s	remaining: 38.1s
937:	learn: 0.0649754	total: 9m 27s	remaining: 37.5s
938:	learn: 0.0649443	total: 9m 28s	remaining: 36.9s
939:	learn: 0.0649088	total: 9m 28s	remaining: 36.3s
940:	learn: 0.0648724	total: 9m 29s	remaining: 3

In [14]:
liste_acc

{'MinMaxScaler et VotingClassifier': 0.7341848223636835,
 'StandardScaler et VotingClassifier': 0.7308825386717219,
 'QuantileTransformer et VotingClassifier': 0.7333204156432247,
 'RobustScaler et VotingClassifier': 0.6903337378384207,
 'Normalizer et VotingClassifier': 0.6428943175461144,
 'MaxAbsScaler et VotingClassifier': 0.7142948274026858,
 'PowerTransformer et VotingClassifier': 0.7358658379000248}

In [15]:
liste_fscore

{'MinMaxScaler et VotingClassifier': 0.7054275830492627,
 'StandardScaler et VotingClassifier': 0.723226647450793,
 'QuantileTransformer et VotingClassifier': 0.7188158153480965,
 'RobustScaler et VotingClassifier': 0.671117384384712,
 'Normalizer et VotingClassifier': 0.625263433802564,
 'MaxAbsScaler et VotingClassifier': 0.6803720073758908,
 'PowerTransformer et VotingClassifier': 0.7213801895984366}

# voting Train house 2 Test house 1 - la nuit

In [16]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

house2_power_blk1 = house2_power_blk1.between_time('22:00', '5:59:59')
house1_power_blk2 = house1_power_blk2.between_time('22:00', '5:59:59')

In [17]:
taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_test = house1_power_blk2.iloc[:,-1]
X_test = house1_power_blk2.iloc[:,:-1]

y_train = house2_power_blk1.iloc[:,-1]
X_train = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [18]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), Normalizer(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "MaxAbsScaler", "PowerTransformer"]

clf2 = HistGradientBoostingClassifier()
clf3 = LGBMClassifier()
clf4 = CatBoostClassifier()

liste_classifier = [VotingClassifier(estimators=[('HGB', clf2), ('LGBM', clf3), ('CBC', clf4)], voting='hard')]
liste_classifier_name = ["VotingClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0
Learning rate set to 0.246968
0:	learn: 0.4239267	total: 164ms	remaining: 2m 43s
1:	learn: 0.3094317	total: 309ms	remaining: 2m 34s
2:	learn: 0.2587223	total: 469ms	remaining: 2m 35s
3:	learn: 0.2226719	total: 617ms	remaining: 2m 33s
4:	learn: 0.2052410	total: 790ms	remaining: 2m 37s
5:	learn: 0.1976028	total: 934ms	remaining: 2m 34s
6:	learn: 0.1893881	total: 1.09s	remaining: 2m 34s
7:	learn: 0.1841512	total: 1.23s	remaining: 2m 31s
8:	learn: 0.1802913	total: 1.39s	remaining: 2m 32s
9:	learn: 0.1758987	total: 1.52s	remaining: 2m 30s
10:	learn: 0.1705514	total: 1.69s	remaining: 2m 31s
11:	learn: 0.1653866	total: 1.84s	remaining: 2m 31s
12:	learn: 0.1617689	total: 1.99s	remaining: 2m 30s
13:	learn: 0.1583276	total: 2.13s	remaining: 2m 29s
14:	learn: 0.1543111	total: 2.29s	remaining: 2m 30s
15:	learn: 0.1527346	total: 2.43s	remaining: 2m 29s
16:	learn: 0.1499769	total: 2.6s	remaining: 2m 30s
17:	learn: 0.1470806	total: 2.76s	remaining: 2m 30s
18:	learn: 0.1439201	total: 2.91s	remaining

157:	learn: 0.0516171	total: 25.5s	remaining: 2m 16s
158:	learn: 0.0515526	total: 25.7s	remaining: 2m 15s
159:	learn: 0.0515061	total: 25.8s	remaining: 2m 15s
160:	learn: 0.0514307	total: 26s	remaining: 2m 15s
161:	learn: 0.0513685	total: 26.1s	remaining: 2m 15s
162:	learn: 0.0511025	total: 26.3s	remaining: 2m 15s
163:	learn: 0.0510426	total: 26.4s	remaining: 2m 14s
164:	learn: 0.0509884	total: 26.6s	remaining: 2m 14s
165:	learn: 0.0508199	total: 26.8s	remaining: 2m 14s
166:	learn: 0.0507539	total: 26.9s	remaining: 2m 14s
167:	learn: 0.0506798	total: 27.1s	remaining: 2m 14s
168:	learn: 0.0505284	total: 27.3s	remaining: 2m 14s
169:	learn: 0.0504271	total: 27.4s	remaining: 2m 13s
170:	learn: 0.0503509	total: 27.6s	remaining: 2m 13s
171:	learn: 0.0502235	total: 27.8s	remaining: 2m 13s
172:	learn: 0.0501134	total: 28s	remaining: 2m 13s
173:	learn: 0.0500086	total: 28.2s	remaining: 2m 13s
174:	learn: 0.0499109	total: 28.4s	remaining: 2m 13s
175:	learn: 0.0497592	total: 28.6s	remaining: 2m 1

314:	learn: 0.0404629	total: 52.7s	remaining: 1m 54s
315:	learn: 0.0404252	total: 52.8s	remaining: 1m 54s
316:	learn: 0.0403327	total: 53s	remaining: 1m 54s
317:	learn: 0.0403237	total: 53.2s	remaining: 1m 54s
318:	learn: 0.0402526	total: 53.3s	remaining: 1m 53s
319:	learn: 0.0402034	total: 53.5s	remaining: 1m 53s
320:	learn: 0.0401507	total: 53.7s	remaining: 1m 53s
321:	learn: 0.0401274	total: 53.8s	remaining: 1m 53s
322:	learn: 0.0400982	total: 54s	remaining: 1m 53s
323:	learn: 0.0400684	total: 54.2s	remaining: 1m 53s
324:	learn: 0.0400429	total: 54.3s	remaining: 1m 52s
325:	learn: 0.0400182	total: 54.5s	remaining: 1m 52s
326:	learn: 0.0400123	total: 54.7s	remaining: 1m 52s
327:	learn: 0.0399755	total: 54.9s	remaining: 1m 52s
328:	learn: 0.0399047	total: 55.1s	remaining: 1m 52s
329:	learn: 0.0398945	total: 55.3s	remaining: 1m 52s
330:	learn: 0.0398589	total: 55.5s	remaining: 1m 52s
331:	learn: 0.0398488	total: 55.7s	remaining: 1m 52s
332:	learn: 0.0398241	total: 55.8s	remaining: 1m 5

469:	learn: 0.0371864	total: 1m 20s	remaining: 1m 30s
470:	learn: 0.0371823	total: 1m 20s	remaining: 1m 30s
471:	learn: 0.0371657	total: 1m 20s	remaining: 1m 29s
472:	learn: 0.0371455	total: 1m 20s	remaining: 1m 29s
473:	learn: 0.0371426	total: 1m 20s	remaining: 1m 29s
474:	learn: 0.0371288	total: 1m 20s	remaining: 1m 29s
475:	learn: 0.0371195	total: 1m 21s	remaining: 1m 29s
476:	learn: 0.0371159	total: 1m 21s	remaining: 1m 29s
477:	learn: 0.0370812	total: 1m 21s	remaining: 1m 28s
478:	learn: 0.0370535	total: 1m 21s	remaining: 1m 28s
479:	learn: 0.0370498	total: 1m 21s	remaining: 1m 28s
480:	learn: 0.0370469	total: 1m 21s	remaining: 1m 28s
481:	learn: 0.0370366	total: 1m 22s	remaining: 1m 28s
482:	learn: 0.0370280	total: 1m 22s	remaining: 1m 28s
483:	learn: 0.0370238	total: 1m 22s	remaining: 1m 27s
484:	learn: 0.0370208	total: 1m 22s	remaining: 1m 27s
485:	learn: 0.0370003	total: 1m 22s	remaining: 1m 27s
486:	learn: 0.0369982	total: 1m 22s	remaining: 1m 27s
487:	learn: 0.0369945	total:

622:	learn: 0.0358891	total: 1m 49s	remaining: 1m 5s
623:	learn: 0.0358808	total: 1m 49s	remaining: 1m 5s
624:	learn: 0.0358604	total: 1m 49s	remaining: 1m 5s
625:	learn: 0.0358557	total: 1m 49s	remaining: 1m 5s
626:	learn: 0.0358529	total: 1m 50s	remaining: 1m 5s
627:	learn: 0.0358496	total: 1m 50s	remaining: 1m 5s
628:	learn: 0.0358469	total: 1m 50s	remaining: 1m 5s
629:	learn: 0.0358469	total: 1m 51s	remaining: 1m 5s
630:	learn: 0.0358229	total: 1m 51s	remaining: 1m 5s
631:	learn: 0.0358141	total: 1m 51s	remaining: 1m 5s
632:	learn: 0.0358141	total: 1m 51s	remaining: 1m 4s
633:	learn: 0.0358111	total: 1m 52s	remaining: 1m 4s
634:	learn: 0.0358111	total: 1m 52s	remaining: 1m 4s
635:	learn: 0.0358080	total: 1m 52s	remaining: 1m 4s
636:	learn: 0.0358044	total: 1m 52s	remaining: 1m 4s
637:	learn: 0.0358008	total: 1m 53s	remaining: 1m 4s
638:	learn: 0.0357950	total: 1m 53s	remaining: 1m 4s
639:	learn: 0.0357931	total: 1m 53s	remaining: 1m 3s
640:	learn: 0.0357853	total: 1m 53s	remaining:

...

310:	learn: 0.0399014	total: 48.1s	remaining: 1m 46s
311:	learn: 0.0398856	total: 48.3s	remaining: 1m 46s
312:	learn: 0.0398695	total: 48.4s	remaining: 1m 46s
313:	learn: 0.0398517	total: 48.6s	remaining: 1m 46s
314:	learn: 0.0398411	total: 48.8s	remaining: 1m 46s
315:	learn: 0.0398336	total: 48.9s	remaining: 1m 45s
316:	learn: 0.0397947	total: 49.1s	remaining: 1m 45s
317:	learn: 0.0397580	total: 49.3s	remaining: 1m 45s
318:	learn: 0.0397439	total: 49.4s	remaining: 1m 45s
319:	learn: 0.0397024	total: 49.6s	remaining: 1m 45s
320:	learn: 0.0396909	total: 49.7s	remaining: 1m 45s
321:	learn: 0.0396234	total: 49.9s	remaining: 1m 45s
322:	learn: 0.0395600	total: 50.1s	remaining: 1m 44s
323:	learn: 0.0394257	total: 50.3s	remaining: 1m 44s
324:	learn: 0.0393728	total: 50.4s	remaining: 1m 44s
325:	learn: 0.0393568	total: 50.6s	remaining: 1m 44s
326:	learn: 0.0393430	total: 50.7s	remaining: 1m 44s
327:	learn: 0.0393180	total: 50.9s	remaining: 1m 44s
328:	learn: 0.0392957	total: 51.1s	remaining: 

465:	learn: 0.0368578	total: 1m 14s	remaining: 1m 25s
466:	learn: 0.0368498	total: 1m 14s	remaining: 1m 25s
467:	learn: 0.0368224	total: 1m 15s	remaining: 1m 25s
468:	learn: 0.0368181	total: 1m 15s	remaining: 1m 25s
469:	learn: 0.0367923	total: 1m 15s	remaining: 1m 25s
470:	learn: 0.0367654	total: 1m 15s	remaining: 1m 24s
471:	learn: 0.0367617	total: 1m 15s	remaining: 1m 24s
472:	learn: 0.0367572	total: 1m 15s	remaining: 1m 24s
473:	learn: 0.0367376	total: 1m 16s	remaining: 1m 24s
474:	learn: 0.0367311	total: 1m 16s	remaining: 1m 24s
475:	learn: 0.0366938	total: 1m 16s	remaining: 1m 24s
476:	learn: 0.0366825	total: 1m 16s	remaining: 1m 23s
477:	learn: 0.0366623	total: 1m 16s	remaining: 1m 23s
478:	learn: 0.0366460	total: 1m 16s	remaining: 1m 23s
479:	learn: 0.0366422	total: 1m 17s	remaining: 1m 23s
480:	learn: 0.0366343	total: 1m 17s	remaining: 1m 23s
481:	learn: 0.0366236	total: 1m 17s	remaining: 1m 23s
482:	learn: 0.0366020	total: 1m 17s	remaining: 1m 23s
483:	learn: 0.0365852	total:

619:	learn: 0.0352488	total: 1m 41s	remaining: 1m 2s
620:	learn: 0.0352398	total: 1m 41s	remaining: 1m 2s
621:	learn: 0.0352281	total: 1m 41s	remaining: 1m 1s
622:	learn: 0.0352237	total: 1m 41s	remaining: 1m 1s
623:	learn: 0.0352156	total: 1m 42s	remaining: 1m 1s
624:	learn: 0.0352155	total: 1m 42s	remaining: 1m 1s
625:	learn: 0.0352138	total: 1m 42s	remaining: 1m 1s
626:	learn: 0.0352116	total: 1m 42s	remaining: 1m 1s
627:	learn: 0.0352091	total: 1m 42s	remaining: 1m
628:	learn: 0.0352050	total: 1m 42s	remaining: 1m
629:	learn: 0.0352026	total: 1m 43s	remaining: 1m
630:	learn: 0.0351978	total: 1m 43s	remaining: 1m
631:	learn: 0.0351978	total: 1m 43s	remaining: 1m
632:	learn: 0.0351978	total: 1m 43s	remaining: 1m
633:	learn: 0.0351957	total: 1m 43s	remaining: 59.9s
634:	learn: 0.0351658	total: 1m 44s	remaining: 59.8s
635:	learn: 0.0351620	total: 1m 44s	remaining: 59.6s
636:	learn: 0.0351526	total: 1m 44s	remaining: 59.5s
637:	learn: 0.0351507	total: 1m 44s	remaining: 59.3s
638:	learn:

777:	learn: 0.0344031	total: 2m 9s	remaining: 36.9s
778:	learn: 0.0344014	total: 2m 9s	remaining: 36.8s
779:	learn: 0.0343965	total: 2m 9s	remaining: 36.6s
780:	learn: 0.0343923	total: 2m 9s	remaining: 36.4s
781:	learn: 0.0343900	total: 2m 10s	remaining: 36.3s
782:	learn: 0.0343899	total: 2m 10s	remaining: 36.1s
783:	learn: 0.0343815	total: 2m 10s	remaining: 35.9s
784:	learn: 0.0343726	total: 2m 10s	remaining: 35.8s
785:	learn: 0.0343716	total: 2m 10s	remaining: 35.6s
786:	learn: 0.0343715	total: 2m 10s	remaining: 35.4s
787:	learn: 0.0343686	total: 2m 11s	remaining: 35.3s
788:	learn: 0.0343427	total: 2m 11s	remaining: 35.1s
789:	learn: 0.0343426	total: 2m 11s	remaining: 34.9s
790:	learn: 0.0343408	total: 2m 11s	remaining: 34.8s
791:	learn: 0.0343363	total: 2m 11s	remaining: 34.6s
792:	learn: 0.0343131	total: 2m 11s	remaining: 34.4s
793:	learn: 0.0343114	total: 2m 12s	remaining: 34.3s
794:	learn: 0.0343113	total: 2m 12s	remaining: 34.1s
795:	learn: 0.0343113	total: 2m 12s	remaining: 33.

932:	learn: 0.0338694	total: 2m 34s	remaining: 11.1s
933:	learn: 0.0338663	total: 2m 35s	remaining: 11s
934:	learn: 0.0338649	total: 2m 35s	remaining: 10.8s
935:	learn: 0.0338631	total: 2m 35s	remaining: 10.6s
936:	learn: 0.0338606	total: 2m 35s	remaining: 10.5s
937:	learn: 0.0338578	total: 2m 35s	remaining: 10.3s
938:	learn: 0.0338549	total: 2m 36s	remaining: 10.1s
939:	learn: 0.0338533	total: 2m 36s	remaining: 9.97s
940:	learn: 0.0338488	total: 2m 36s	remaining: 9.8s
941:	learn: 0.0338459	total: 2m 36s	remaining: 9.64s
942:	learn: 0.0338424	total: 2m 36s	remaining: 9.48s
943:	learn: 0.0338393	total: 2m 36s	remaining: 9.31s
944:	learn: 0.0338368	total: 2m 37s	remaining: 9.14s
945:	learn: 0.0338274	total: 2m 37s	remaining: 8.98s
946:	learn: 0.0338256	total: 2m 37s	remaining: 8.81s
947:	learn: 0.0338145	total: 2m 37s	remaining: 8.65s
948:	learn: 0.0338083	total: 2m 37s	remaining: 8.48s
949:	learn: 0.0338061	total: 2m 37s	remaining: 8.31s
950:	learn: 0.0338041	total: 2m 38s	remaining: 8.

In [19]:
liste_acc

{'MinMaxScaler et VotingClassifier': 0.8445113886442143,
 'StandardScaler et VotingClassifier': 0.8395511363793251,
 'QuantileTransformer et VotingClassifier': 0.8604099304449151,
 'RobustScaler et VotingClassifier': 0.7849298236409975,
 'MaxAbsScaler et VotingClassifier': 0.7315687308613068,
 'PowerTransformer et VotingClassifier': 0.8359427765152875}

In [20]:
liste_fscore

{'MinMaxScaler et VotingClassifier': 0.5518071773717795,
 'StandardScaler et VotingClassifier': 0.5260214626597496,
 'QuantileTransformer et VotingClassifier': 0.5792693494159648,
 'RobustScaler et VotingClassifier': 0.396944657429213,
 'MaxAbsScaler et VotingClassifier': 0.30976207048423504,
 'PowerTransformer et VotingClassifier': 0.5361649616906626}

# voting Train house 2 Test house 1 - le jour

In [21]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

house2_power_blk1 = house2_power_blk1.between_time('6:00:00', '21:59:59')
house1_power_blk2 = house1_power_blk2.between_time('6:00:00', '21:59:59')

In [22]:
taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_test = house1_power_blk2.iloc[:,-1]
X_test = house1_power_blk2.iloc[:,:-1]

y_train = house2_power_blk1.iloc[:,-1]
X_train = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [23]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), Normalizer(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "MaxAbsScaler", "PowerTransformer"]

clf2 = HistGradientBoostingClassifier()
clf3 = LGBMClassifier()
clf4 = CatBoostClassifier()

liste_classifier = [VotingClassifier(estimators=[('HGB', clf2), ('LGBM', clf3), ('CBC', clf4)], voting='hard')]
liste_classifier_name = ["VotingClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0
Learning rate set to 0.331732
0:	learn: 0.5284390	total: 271ms	remaining: 4m 30s
1:	learn: 0.4679119	total: 546ms	remaining: 4m 32s
2:	learn: 0.4423416	total: 810ms	remaining: 4m 29s
3:	learn: 0.4272060	total: 1.07s	remaining: 4m 25s
4:	learn: 0.4142835	total: 1.36s	remaining: 4m 30s
5:	learn: 0.4011103	total: 1.65s	remaining: 4m 33s
6:	learn: 0.3955222	total: 1.92s	remaining: 4m 31s
7:	learn: 0.3886363	total: 2.19s	remaining: 4m 31s
8:	learn: 0.3827673	total: 2.48s	remaining: 4m 33s
9:	learn: 0.3752307	total: 2.75s	remaining: 4m 32s
10:	learn: 0.3686485	total: 3.04s	remaining: 4m 33s
11:	learn: 0.3651976	total: 3.31s	remaining: 4m 32s
12:	learn: 0.3620831	total: 3.57s	remaining: 4m 31s
13:	learn: 0.3587764	total: 3.83s	remaining: 4m 29s
14:	learn: 0.3532673	total: 4.1s	remaining: 4m 29s
15:	learn: 0.3488356	total: 4.4s	remaining: 4m 30s
16:	learn: 0.3422839	total: 4.67s	remaining: 4m 30s
17:	learn: 0.3399971	total: 4.94s	remaining: 4m 29s
18:	learn: 0.3342681	total: 5.23s	remaining:

158:	learn: 0.1560101	total: 46.6s	remaining: 4m 6s
159:	learn: 0.1557886	total: 46.9s	remaining: 4m 6s
160:	learn: 0.1553008	total: 47.2s	remaining: 4m 5s
161:	learn: 0.1545804	total: 47.5s	remaining: 4m 5s
162:	learn: 0.1540842	total: 47.9s	remaining: 4m 5s
163:	learn: 0.1533589	total: 48.2s	remaining: 4m 5s
164:	learn: 0.1529509	total: 48.6s	remaining: 4m 5s
165:	learn: 0.1525617	total: 48.9s	remaining: 4m 5s
166:	learn: 0.1522257	total: 49.3s	remaining: 4m 5s
167:	learn: 0.1518298	total: 49.6s	remaining: 4m 5s
168:	learn: 0.1514437	total: 50s	remaining: 4m 5s
169:	learn: 0.1506834	total: 50.4s	remaining: 4m 5s
170:	learn: 0.1500261	total: 50.7s	remaining: 4m 5s
171:	learn: 0.1494840	total: 51.1s	remaining: 4m 6s
172:	learn: 0.1490580	total: 51.5s	remaining: 4m 6s
173:	learn: 0.1486226	total: 51.8s	remaining: 4m 6s
174:	learn: 0.1483746	total: 52.1s	remaining: 4m 5s
175:	learn: 0.1480350	total: 52.4s	remaining: 4m 5s
176:	learn: 0.1472949	total: 52.7s	remaining: 4m 5s
177:	learn: 0.

313:	learn: 0.1085270	total: 1m 35s	remaining: 3m 29s
314:	learn: 0.1084347	total: 1m 36s	remaining: 3m 29s
315:	learn: 0.1082823	total: 1m 36s	remaining: 3m 29s
316:	learn: 0.1080980	total: 1m 36s	remaining: 3m 28s
317:	learn: 0.1079076	total: 1m 37s	remaining: 3m 28s
318:	learn: 0.1077029	total: 1m 37s	remaining: 3m 28s
319:	learn: 0.1075609	total: 1m 37s	remaining: 3m 28s
320:	learn: 0.1074695	total: 1m 38s	remaining: 3m 27s
321:	learn: 0.1072909	total: 1m 38s	remaining: 3m 27s
322:	learn: 0.1069212	total: 1m 38s	remaining: 3m 27s
323:	learn: 0.1067463	total: 1m 39s	remaining: 3m 27s
324:	learn: 0.1064835	total: 1m 39s	remaining: 3m 26s
325:	learn: 0.1061053	total: 1m 39s	remaining: 3m 26s
326:	learn: 0.1058976	total: 1m 40s	remaining: 3m 26s
327:	learn: 0.1058003	total: 1m 40s	remaining: 3m 26s
328:	learn: 0.1055965	total: 1m 40s	remaining: 3m 25s
329:	learn: 0.1054503	total: 1m 41s	remaining: 3m 25s
330:	learn: 0.1052271	total: 1m 41s	remaining: 3m 25s
331:	learn: 0.1050940	total:

467:	learn: 0.0908820	total: 2m 28s	remaining: 2m 48s
468:	learn: 0.0908405	total: 2m 28s	remaining: 2m 48s
469:	learn: 0.0907579	total: 2m 28s	remaining: 2m 47s
470:	learn: 0.0907231	total: 2m 29s	remaining: 2m 47s
471:	learn: 0.0906917	total: 2m 29s	remaining: 2m 47s
472:	learn: 0.0905743	total: 2m 29s	remaining: 2m 46s
473:	learn: 0.0905417	total: 2m 30s	remaining: 2m 46s
474:	learn: 0.0904066	total: 2m 30s	remaining: 2m 46s
475:	learn: 0.0902936	total: 2m 30s	remaining: 2m 46s
476:	learn: 0.0901964	total: 2m 31s	remaining: 2m 45s
477:	learn: 0.0901655	total: 2m 31s	remaining: 2m 45s
478:	learn: 0.0900722	total: 2m 31s	remaining: 2m 45s
479:	learn: 0.0899902	total: 2m 32s	remaining: 2m 44s
480:	learn: 0.0898597	total: 2m 32s	remaining: 2m 44s
481:	learn: 0.0897702	total: 2m 32s	remaining: 2m 44s
482:	learn: 0.0896642	total: 2m 33s	remaining: 2m 44s
483:	learn: 0.0895288	total: 2m 33s	remaining: 2m 43s
484:	learn: 0.0894212	total: 2m 34s	remaining: 2m 43s
485:	learn: 0.0893038	total:

620:	learn: 0.0813653	total: 3m 20s	remaining: 2m 2s
621:	learn: 0.0813007	total: 3m 21s	remaining: 2m 2s
622:	learn: 0.0812753	total: 3m 21s	remaining: 2m 1s
623:	learn: 0.0812048	total: 3m 21s	remaining: 2m 1s
624:	learn: 0.0811527	total: 3m 22s	remaining: 2m 1s
625:	learn: 0.0811371	total: 3m 22s	remaining: 2m
626:	learn: 0.0811108	total: 3m 22s	remaining: 2m
627:	learn: 0.0810758	total: 3m 23s	remaining: 2m
628:	learn: 0.0810473	total: 3m 23s	remaining: 2m
629:	learn: 0.0808935	total: 3m 23s	remaining: 1m 59s
630:	learn: 0.0808343	total: 3m 24s	remaining: 1m 59s
631:	learn: 0.0807885	total: 3m 24s	remaining: 1m 59s
632:	learn: 0.0806742	total: 3m 24s	remaining: 1m 58s
633:	learn: 0.0806611	total: 3m 25s	remaining: 1m 58s
634:	learn: 0.0806281	total: 3m 25s	remaining: 1m 58s
635:	learn: 0.0805715	total: 3m 25s	remaining: 1m 57s
636:	learn: 0.0805324	total: 3m 26s	remaining: 1m 57s
637:	learn: 0.0804847	total: 3m 26s	remaining: 1m 57s
638:	learn: 0.0804359	total: 3m 26s	remaining: 1m

...

261:	learn: 0.1222593	total: 1m 49s	remaining: 5m 7s
262:	learn: 0.1221917	total: 1m 49s	remaining: 5m 7s
263:	learn: 0.1219208	total: 1m 50s	remaining: 5m 7s
264:	learn: 0.1218062	total: 1m 50s	remaining: 5m 6s
265:	learn: 0.1214485	total: 1m 51s	remaining: 5m 6s
266:	learn: 0.1211646	total: 1m 51s	remaining: 5m 6s
267:	learn: 0.1209643	total: 1m 51s	remaining: 5m 5s
268:	learn: 0.1207651	total: 1m 52s	remaining: 5m 5s
269:	learn: 0.1206239	total: 1m 52s	remaining: 5m 5s
270:	learn: 0.1204032	total: 1m 53s	remaining: 5m 5s
271:	learn: 0.1201567	total: 1m 54s	remaining: 5m 5s
272:	learn: 0.1199848	total: 1m 54s	remaining: 5m 5s
273:	learn: 0.1197127	total: 1m 55s	remaining: 5m 5s
274:	learn: 0.1193832	total: 1m 55s	remaining: 5m 4s
275:	learn: 0.1191488	total: 1m 56s	remaining: 5m 4s
276:	learn: 0.1189964	total: 1m 56s	remaining: 5m 4s
277:	learn: 0.1188262	total: 1m 56s	remaining: 5m 3s
278:	learn: 0.1186554	total: 1m 57s	remaining: 5m 3s
279:	learn: 0.1184026	total: 1m 57s	remaining:

414:	learn: 0.0977716	total: 2m 59s	remaining: 4m 13s
415:	learn: 0.0976556	total: 3m	remaining: 4m 13s
416:	learn: 0.0975924	total: 3m	remaining: 4m 12s
417:	learn: 0.0974003	total: 3m 1s	remaining: 4m 12s
418:	learn: 0.0972106	total: 3m 1s	remaining: 4m 11s
419:	learn: 0.0971048	total: 3m 1s	remaining: 4m 11s
420:	learn: 0.0969824	total: 3m 2s	remaining: 4m 10s
421:	learn: 0.0967977	total: 3m 2s	remaining: 4m 10s
422:	learn: 0.0966926	total: 3m 2s	remaining: 4m 9s
423:	learn: 0.0965888	total: 3m 3s	remaining: 4m 9s
424:	learn: 0.0964555	total: 3m 3s	remaining: 4m 8s
425:	learn: 0.0963896	total: 3m 4s	remaining: 4m 8s
426:	learn: 0.0961997	total: 3m 4s	remaining: 4m 7s
427:	learn: 0.0961010	total: 3m 4s	remaining: 4m 7s
428:	learn: 0.0960205	total: 3m 5s	remaining: 4m 6s
429:	learn: 0.0959506	total: 3m 5s	remaining: 4m 6s
430:	learn: 0.0958617	total: 3m 5s	remaining: 4m 5s
431:	learn: 0.0958099	total: 3m 6s	remaining: 4m 4s
432:	learn: 0.0957373	total: 3m 6s	remaining: 4m 4s
433:	lear

568:	learn: 0.0851996	total: 3m 58s	remaining: 3m
569:	learn: 0.0850720	total: 3m 58s	remaining: 3m
570:	learn: 0.0850249	total: 3m 59s	remaining: 2m 59s
571:	learn: 0.0849306	total: 3m 59s	remaining: 2m 59s
572:	learn: 0.0848361	total: 4m	remaining: 2m 58s
573:	learn: 0.0847581	total: 4m	remaining: 2m 58s
574:	learn: 0.0846825	total: 4m	remaining: 2m 58s
575:	learn: 0.0846261	total: 4m 1s	remaining: 2m 57s
576:	learn: 0.0845860	total: 4m 1s	remaining: 2m 57s
577:	learn: 0.0845169	total: 4m 1s	remaining: 2m 56s
578:	learn: 0.0844802	total: 4m 2s	remaining: 2m 56s
579:	learn: 0.0844317	total: 4m 2s	remaining: 2m 55s
580:	learn: 0.0843772	total: 4m 3s	remaining: 2m 55s
581:	learn: 0.0842250	total: 4m 3s	remaining: 2m 54s
582:	learn: 0.0841475	total: 4m 3s	remaining: 2m 54s
583:	learn: 0.0841227	total: 4m 4s	remaining: 2m 53s
584:	learn: 0.0840895	total: 4m 4s	remaining: 2m 53s
585:	learn: 0.0840809	total: 4m 4s	remaining: 2m 52s
586:	learn: 0.0840188	total: 4m 5s	remaining: 2m 52s
587:	l

722:	learn: 0.0776699	total: 4m 53s	remaining: 1m 52s
723:	learn: 0.0776389	total: 4m 53s	remaining: 1m 52s
724:	learn: 0.0776180	total: 4m 54s	remaining: 1m 51s
725:	learn: 0.0775963	total: 4m 54s	remaining: 1m 51s
726:	learn: 0.0775778	total: 4m 54s	remaining: 1m 50s
727:	learn: 0.0775277	total: 4m 55s	remaining: 1m 50s
728:	learn: 0.0774812	total: 4m 55s	remaining: 1m 49s
729:	learn: 0.0774592	total: 4m 55s	remaining: 1m 49s
730:	learn: 0.0774151	total: 4m 56s	remaining: 1m 49s
731:	learn: 0.0774102	total: 4m 56s	remaining: 1m 48s
732:	learn: 0.0773786	total: 4m 56s	remaining: 1m 48s
733:	learn: 0.0773489	total: 4m 57s	remaining: 1m 47s
734:	learn: 0.0773352	total: 4m 57s	remaining: 1m 47s
735:	learn: 0.0772832	total: 4m 57s	remaining: 1m 46s
736:	learn: 0.0772528	total: 4m 58s	remaining: 1m 46s
737:	learn: 0.0771673	total: 4m 58s	remaining: 1m 46s
738:	learn: 0.0771357	total: 4m 59s	remaining: 1m 45s
739:	learn: 0.0770666	total: 4m 59s	remaining: 1m 45s
740:	learn: 0.0770147	total:

876:	learn: 0.0727488	total: 5m 45s	remaining: 48.4s
877:	learn: 0.0727268	total: 5m 45s	remaining: 48s
878:	learn: 0.0726878	total: 5m 45s	remaining: 47.6s
879:	learn: 0.0726739	total: 5m 46s	remaining: 47.2s
880:	learn: 0.0726183	total: 5m 46s	remaining: 46.8s
881:	learn: 0.0725430	total: 5m 46s	remaining: 46.4s
882:	learn: 0.0725221	total: 5m 47s	remaining: 46s
883:	learn: 0.0725052	total: 5m 47s	remaining: 45.6s
884:	learn: 0.0724695	total: 5m 47s	remaining: 45.2s
885:	learn: 0.0724452	total: 5m 48s	remaining: 44.8s
886:	learn: 0.0724386	total: 5m 48s	remaining: 44.4s
887:	learn: 0.0724122	total: 5m 48s	remaining: 44s
888:	learn: 0.0723908	total: 5m 49s	remaining: 43.6s
889:	learn: 0.0723509	total: 5m 49s	remaining: 43.2s
890:	learn: 0.0723329	total: 5m 49s	remaining: 42.8s
891:	learn: 0.0723203	total: 5m 50s	remaining: 42.4s
892:	learn: 0.0722851	total: 5m 50s	remaining: 42s
893:	learn: 0.0722723	total: 5m 50s	remaining: 41.6s
894:	learn: 0.0722502	total: 5m 51s	remaining: 41.2s
8

In [24]:
liste_acc

{'MinMaxScaler et VotingClassifier': 0.674891850525825,
 'StandardScaler et VotingClassifier': 0.6857856124410062,
 'QuantileTransformer et VotingClassifier': 0.6900765933618351,
 'RobustScaler et VotingClassifier': 0.6918749968997794,
 'MaxAbsScaler et VotingClassifier': 0.6246101300328981,
 'PowerTransformer et VotingClassifier': 0.6687024322815364}

In [25]:
liste_fscore

{'MinMaxScaler et VotingClassifier': 0.724364796091773,
 'StandardScaler et VotingClassifier': 0.7646689204504183,
 'QuantileTransformer et VotingClassifier': 0.7528660451770417,
 'RobustScaler et VotingClassifier': 0.7462339802789563,
 'MaxAbsScaler et VotingClassifier': 0.6778686126710748,
 'PowerTransformer et VotingClassifier': 0.7091616193003382}

# voting Train house 1 Test house 2 - la nuit

In [8]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

house2_power_blk1 = house2_power_blk1.between_time('22:00', '5:59:59')
house1_power_blk2 = house1_power_blk2.between_time('22:00', '5:59:59')

In [9]:
taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_train = house1_power_blk2.iloc[:,-1]
X_train = house1_power_blk2.iloc[:,:-1]

y_test = house2_power_blk1.iloc[:,-1]
X_test = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [10]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), Normalizer(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "MaxAbsScaler", "PowerTransformer"]

clf2 = HistGradientBoostingClassifier()
clf3 = LGBMClassifier()
clf4 = CatBoostClassifier()

liste_classifier = [VotingClassifier(estimators=[('HGB', clf2), ('LGBM', clf3), ('CBC', clf4)], voting='hard')]
liste_classifier_name = ["VotingClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0
Learning rate set to 0.253539
0:	learn: 0.3955183	total: 301ms	remaining: 5m
1:	learn: 0.2766588	total: 460ms	remaining: 3m 49s
2:	learn: 0.2350256	total: 608ms	remaining: 3m 22s
3:	learn: 0.2123539	total: 756ms	remaining: 3m 8s
4:	learn: 0.1948234	total: 909ms	remaining: 3m
5:	learn: 0.1855632	total: 1.05s	remaining: 2m 54s
6:	learn: 0.1763402	total: 1.22s	remaining: 2m 52s
7:	learn: 0.1704941	total: 1.37s	remaining: 2m 50s
8:	learn: 0.1636217	total: 1.53s	remaining: 2m 48s
9:	learn: 0.1611709	total: 1.69s	remaining: 2m 46s
10:	learn: 0.1568143	total: 1.85s	remaining: 2m 46s
11:	learn: 0.1523538	total: 2.01s	remaining: 2m 45s
12:	learn: 0.1473761	total: 2.17s	remaining: 2m 44s
13:	learn: 0.1447189	total: 2.32s	remaining: 2m 43s
14:	learn: 0.1412266	total: 2.47s	remaining: 2m 42s
15:	learn: 0.1382691	total: 2.63s	remaining: 2m 42s
16:	learn: 0.1325173	total: 2.79s	remaining: 2m 41s
17:	learn: 0.1308035	total: 2.95s	remaining: 2m 40s
18:	learn: 0.1283924	total: 3.1s	remaining: 2m 40s


158:	learn: 0.0497908	total: 25.9s	remaining: 2m 16s
159:	learn: 0.0496693	total: 26s	remaining: 2m 16s
160:	learn: 0.0495407	total: 26.2s	remaining: 2m 16s
161:	learn: 0.0494646	total: 26.3s	remaining: 2m 16s
162:	learn: 0.0493744	total: 26.5s	remaining: 2m 16s
163:	learn: 0.0491546	total: 26.7s	remaining: 2m 15s
164:	learn: 0.0490746	total: 26.8s	remaining: 2m 15s
165:	learn: 0.0489659	total: 27s	remaining: 2m 15s
166:	learn: 0.0488844	total: 27.1s	remaining: 2m 15s
167:	learn: 0.0487835	total: 27.3s	remaining: 2m 15s
168:	learn: 0.0485926	total: 27.5s	remaining: 2m 14s
169:	learn: 0.0481805	total: 27.6s	remaining: 2m 14s
170:	learn: 0.0480014	total: 27.8s	remaining: 2m 14s
171:	learn: 0.0478818	total: 27.9s	remaining: 2m 14s
172:	learn: 0.0477934	total: 28.1s	remaining: 2m 14s
173:	learn: 0.0476029	total: 28.3s	remaining: 2m 14s
174:	learn: 0.0474817	total: 28.4s	remaining: 2m 14s
175:	learn: 0.0473721	total: 28.6s	remaining: 2m 13s
176:	learn: 0.0473146	total: 28.8s	remaining: 2m 1

316:	learn: 0.0377663	total: 52.9s	remaining: 1m 53s
317:	learn: 0.0377170	total: 53.1s	remaining: 1m 53s
318:	learn: 0.0376897	total: 53.2s	remaining: 1m 53s
319:	learn: 0.0376669	total: 53.4s	remaining: 1m 53s
320:	learn: 0.0376414	total: 53.6s	remaining: 1m 53s
321:	learn: 0.0375325	total: 53.8s	remaining: 1m 53s
322:	learn: 0.0374568	total: 53.9s	remaining: 1m 53s
323:	learn: 0.0374368	total: 54.1s	remaining: 1m 52s
324:	learn: 0.0374081	total: 54.3s	remaining: 1m 52s
325:	learn: 0.0373734	total: 54.4s	remaining: 1m 52s
326:	learn: 0.0373324	total: 54.6s	remaining: 1m 52s
327:	learn: 0.0372777	total: 54.8s	remaining: 1m 52s
328:	learn: 0.0372247	total: 54.9s	remaining: 1m 52s
329:	learn: 0.0371809	total: 55.1s	remaining: 1m 51s
330:	learn: 0.0371332	total: 55.3s	remaining: 1m 51s
331:	learn: 0.0370867	total: 55.5s	remaining: 1m 51s
332:	learn: 0.0370779	total: 55.6s	remaining: 1m 51s
333:	learn: 0.0370527	total: 55.8s	remaining: 1m 51s
334:	learn: 0.0370153	total: 56s	remaining: 1m

470:	learn: 0.0326070	total: 1m 20s	remaining: 1m 29s
471:	learn: 0.0325927	total: 1m 20s	remaining: 1m 29s
472:	learn: 0.0325697	total: 1m 20s	remaining: 1m 29s
473:	learn: 0.0325581	total: 1m 20s	remaining: 1m 29s
474:	learn: 0.0325132	total: 1m 20s	remaining: 1m 29s
475:	learn: 0.0324991	total: 1m 21s	remaining: 1m 29s
476:	learn: 0.0324849	total: 1m 21s	remaining: 1m 29s
477:	learn: 0.0324559	total: 1m 21s	remaining: 1m 28s
478:	learn: 0.0324453	total: 1m 21s	remaining: 1m 28s
479:	learn: 0.0324295	total: 1m 21s	remaining: 1m 28s
480:	learn: 0.0324116	total: 1m 21s	remaining: 1m 28s
481:	learn: 0.0323945	total: 1m 22s	remaining: 1m 28s
482:	learn: 0.0323667	total: 1m 22s	remaining: 1m 28s
483:	learn: 0.0323513	total: 1m 22s	remaining: 1m 27s
484:	learn: 0.0323418	total: 1m 22s	remaining: 1m 27s
485:	learn: 0.0323164	total: 1m 22s	remaining: 1m 27s
486:	learn: 0.0323015	total: 1m 23s	remaining: 1m 27s
487:	learn: 0.0322885	total: 1m 23s	remaining: 1m 27s
488:	learn: 0.0322656	total:

623:	learn: 0.0301483	total: 1m 50s	remaining: 1m 6s
624:	learn: 0.0301439	total: 1m 50s	remaining: 1m 6s
625:	learn: 0.0301340	total: 1m 50s	remaining: 1m 6s
626:	learn: 0.0301262	total: 1m 51s	remaining: 1m 6s
627:	learn: 0.0301083	total: 1m 51s	remaining: 1m 5s
628:	learn: 0.0300920	total: 1m 51s	remaining: 1m 5s
629:	learn: 0.0300807	total: 1m 51s	remaining: 1m 5s
630:	learn: 0.0300715	total: 1m 51s	remaining: 1m 5s
631:	learn: 0.0300551	total: 1m 52s	remaining: 1m 5s
632:	learn: 0.0300482	total: 1m 52s	remaining: 1m 5s
633:	learn: 0.0300329	total: 1m 52s	remaining: 1m 4s
634:	learn: 0.0300255	total: 1m 52s	remaining: 1m 4s
635:	learn: 0.0300113	total: 1m 52s	remaining: 1m 4s
636:	learn: 0.0300023	total: 1m 53s	remaining: 1m 4s
637:	learn: 0.0299892	total: 1m 53s	remaining: 1m 4s
638:	learn: 0.0299791	total: 1m 53s	remaining: 1m 4s
639:	learn: 0.0299662	total: 1m 53s	remaining: 1m 3s
640:	learn: 0.0299477	total: 1m 53s	remaining: 1m 3s
641:	learn: 0.0299373	total: 1m 53s	remaining:

...

315:	learn: 0.0371342	total: 59.4s	remaining: 2m 8s
316:	learn: 0.0370551	total: 59.6s	remaining: 2m 8s
317:	learn: 0.0370289	total: 59.8s	remaining: 2m 8s
318:	learn: 0.0370029	total: 60s	remaining: 2m 8s
319:	learn: 0.0369696	total: 1m	remaining: 2m 7s
320:	learn: 0.0369280	total: 1m	remaining: 2m 7s
321:	learn: 0.0368514	total: 1m	remaining: 2m 7s
322:	learn: 0.0368280	total: 1m	remaining: 2m 7s
323:	learn: 0.0367746	total: 1m	remaining: 2m 7s
324:	learn: 0.0367560	total: 1m 1s	remaining: 2m 6s
325:	learn: 0.0367295	total: 1m 1s	remaining: 2m 6s
326:	learn: 0.0366889	total: 1m 1s	remaining: 2m 6s
327:	learn: 0.0366179	total: 1m 1s	remaining: 2m 6s
328:	learn: 0.0365830	total: 1m 1s	remaining: 2m 6s
329:	learn: 0.0365426	total: 1m 2s	remaining: 2m 5s
330:	learn: 0.0364725	total: 1m 2s	remaining: 2m 5s
331:	learn: 0.0364219	total: 1m 2s	remaining: 2m 5s
332:	learn: 0.0363826	total: 1m 2s	remaining: 2m 5s
333:	learn: 0.0363472	total: 1m 2s	remaining: 2m 5s
334:	learn: 0.0363019	total: 

470:	learn: 0.0323573	total: 1m 28s	remaining: 1m 39s
471:	learn: 0.0323307	total: 1m 28s	remaining: 1m 39s
472:	learn: 0.0322885	total: 1m 28s	remaining: 1m 38s
473:	learn: 0.0322642	total: 1m 28s	remaining: 1m 38s
474:	learn: 0.0322492	total: 1m 29s	remaining: 1m 38s
475:	learn: 0.0322326	total: 1m 29s	remaining: 1m 38s
476:	learn: 0.0322247	total: 1m 29s	remaining: 1m 38s
477:	learn: 0.0321712	total: 1m 29s	remaining: 1m 37s
478:	learn: 0.0321654	total: 1m 29s	remaining: 1m 37s
479:	learn: 0.0321401	total: 1m 30s	remaining: 1m 37s
480:	learn: 0.0321308	total: 1m 30s	remaining: 1m 37s
481:	learn: 0.0321199	total: 1m 30s	remaining: 1m 37s
482:	learn: 0.0321147	total: 1m 30s	remaining: 1m 36s
483:	learn: 0.0321012	total: 1m 30s	remaining: 1m 36s
484:	learn: 0.0320786	total: 1m 30s	remaining: 1m 36s
485:	learn: 0.0320741	total: 1m 31s	remaining: 1m 36s
486:	learn: 0.0320635	total: 1m 31s	remaining: 1m 36s
487:	learn: 0.0320389	total: 1m 31s	remaining: 1m 35s
488:	learn: 0.0319876	total:

622:	learn: 0.0299655	total: 1m 56s	remaining: 1m 10s
623:	learn: 0.0299495	total: 1m 57s	remaining: 1m 10s
624:	learn: 0.0299427	total: 1m 57s	remaining: 1m 10s
625:	learn: 0.0299359	total: 1m 57s	remaining: 1m 10s
626:	learn: 0.0299331	total: 1m 57s	remaining: 1m 10s
627:	learn: 0.0299145	total: 1m 57s	remaining: 1m 9s
628:	learn: 0.0298987	total: 1m 58s	remaining: 1m 9s
629:	learn: 0.0298928	total: 1m 58s	remaining: 1m 9s
630:	learn: 0.0298847	total: 1m 58s	remaining: 1m 9s
631:	learn: 0.0298730	total: 1m 58s	remaining: 1m 9s
632:	learn: 0.0298586	total: 1m 58s	remaining: 1m 8s
633:	learn: 0.0298494	total: 1m 59s	remaining: 1m 8s
634:	learn: 0.0298405	total: 1m 59s	remaining: 1m 8s
635:	learn: 0.0298277	total: 1m 59s	remaining: 1m 8s
636:	learn: 0.0298232	total: 1m 59s	remaining: 1m 8s
637:	learn: 0.0298069	total: 1m 59s	remaining: 1m 7s
638:	learn: 0.0297931	total: 1m 59s	remaining: 1m 7s
639:	learn: 0.0297860	total: 2m	remaining: 1m 7s
640:	learn: 0.0297742	total: 2m	remaining: 1m

779:	learn: 0.0284417	total: 2m 26s	remaining: 41.3s
780:	learn: 0.0284194	total: 2m 26s	remaining: 41.1s
781:	learn: 0.0284026	total: 2m 26s	remaining: 40.9s
782:	learn: 0.0283976	total: 2m 26s	remaining: 40.7s
783:	learn: 0.0283881	total: 2m 27s	remaining: 40.5s
784:	learn: 0.0283619	total: 2m 27s	remaining: 40.4s
785:	learn: 0.0283590	total: 2m 27s	remaining: 40.2s
786:	learn: 0.0283543	total: 2m 27s	remaining: 40s
787:	learn: 0.0283244	total: 2m 27s	remaining: 39.8s
788:	learn: 0.0283163	total: 2m 28s	remaining: 39.6s
789:	learn: 0.0283108	total: 2m 28s	remaining: 39.4s
790:	learn: 0.0282970	total: 2m 28s	remaining: 39.2s
791:	learn: 0.0282908	total: 2m 28s	remaining: 39s
792:	learn: 0.0282852	total: 2m 28s	remaining: 38.9s
793:	learn: 0.0282794	total: 2m 29s	remaining: 38.7s
794:	learn: 0.0282731	total: 2m 29s	remaining: 38.5s
795:	learn: 0.0282633	total: 2m 29s	remaining: 38.3s
796:	learn: 0.0282597	total: 2m 29s	remaining: 38.1s
797:	learn: 0.0282500	total: 2m 29s	remaining: 37.

936:	learn: 0.0272111	total: 2m 55s	remaining: 11.8s
937:	learn: 0.0272078	total: 2m 55s	remaining: 11.6s
938:	learn: 0.0272059	total: 2m 56s	remaining: 11.4s
939:	learn: 0.0272036	total: 2m 56s	remaining: 11.2s
940:	learn: 0.0271960	total: 2m 56s	remaining: 11.1s
941:	learn: 0.0271811	total: 2m 56s	remaining: 10.9s
942:	learn: 0.0271810	total: 2m 56s	remaining: 10.7s
943:	learn: 0.0271769	total: 2m 56s	remaining: 10.5s
944:	learn: 0.0271668	total: 2m 57s	remaining: 10.3s
945:	learn: 0.0271643	total: 2m 57s	remaining: 10.1s
946:	learn: 0.0271630	total: 2m 57s	remaining: 9.93s
947:	learn: 0.0271453	total: 2m 57s	remaining: 9.74s
948:	learn: 0.0271382	total: 2m 57s	remaining: 9.56s
949:	learn: 0.0271331	total: 2m 58s	remaining: 9.37s
950:	learn: 0.0271272	total: 2m 58s	remaining: 9.18s
951:	learn: 0.0271228	total: 2m 58s	remaining: 9s
952:	learn: 0.0271182	total: 2m 58s	remaining: 8.81s
953:	learn: 0.0271162	total: 2m 58s	remaining: 8.62s
954:	learn: 0.0271099	total: 2m 58s	remaining: 8.

In [11]:
liste_acc

{'MinMaxScaler et VotingClassifier': 0.7627220171999465,
 'StandardScaler et VotingClassifier': 0.8668994994115561,
 'QuantileTransformer et VotingClassifier': 0.8546185215375183,
 'RobustScaler et VotingClassifier': 0.7744750398755929,
 'MaxAbsScaler et VotingClassifier': 0.8544617206054043,
 'PowerTransformer et VotingClassifier': 0.7634784201983091}

In [12]:
liste_fscore

{'MinMaxScaler et VotingClassifier': 0.3427392485120784,
 'StandardScaler et VotingClassifier': 0.5340034099534899,
 'QuantileTransformer et VotingClassifier': 0.49193564508320753,
 'RobustScaler et VotingClassifier': 0.1851990265561532,
 'MaxAbsScaler et VotingClassifier': 0.12297209498219003,
 'PowerTransformer et VotingClassifier': 0.33608482695171565}

# voting Train house 1 Test house 2 - le jour

In [13]:
house1_power_blk2 = house1_power_blk2_copy.copy()
house2_power_blk1 = house2_power_blk1_copy.copy()

house2_power_blk1 = house2_power_blk1.between_time('6:00:00', '21:59:59')
house1_power_blk2 = house1_power_blk2.between_time('6:00:00', '21:59:59')

In [14]:
taux = 1
seed = 8

house1_power_blk2 = house1_power_blk2.sample(n=int(round(house1_power_blk2.shape[0] * taux,0)), random_state=seed)
house2_power_blk1 = house2_power_blk1.sample(n=int(round(house2_power_blk1.shape[0] * taux,0)), random_state=seed)

y_train = house1_power_blk2.iloc[:,-1]
X_train = house1_power_blk2.iloc[:,:-1]

y_test = house2_power_blk1.iloc[:,-1]
X_test = house2_power_blk1.iloc[:,:-1]

def calculus_function(para_classifier, para_scaler):

    scaler = para_scaler
    
    X_train_scaled = scaler.fit_transform(X_train)

    X_test_scaled = scaler.fit_transform(X_test)
    
    clf = para_classifier
    
    clf.fit(X_train_scaled, y_train.ravel())
    
    y_pred = clf.predict(X_test_scaled)

    acc = accuracy_score(y_test, y_pred)
    fscore = fbeta_score(y_test, y_pred, beta=0.5)
    
    return acc, fscore

In [15]:
liste_scaler = [MinMaxScaler(), StandardScaler(), QuantileTransformer(), RobustScaler(), Normalizer(), MaxAbsScaler(), PowerTransformer()]
liste_scaler_name = ["MinMaxScaler", "StandardScaler", "QuantileTransformer", "RobustScaler", "MaxAbsScaler", "PowerTransformer"]

clf2 = HistGradientBoostingClassifier()
clf3 = LGBMClassifier()
clf4 = CatBoostClassifier()

liste_classifier = [VotingClassifier(estimators=[('HGB', clf2), ('LGBM', clf3), ('CBC', clf4)], voting='hard')]
liste_classifier_name = ["VotingClassifier"]

liste_acc = dict()

liste_fscore = dict()

n=0
    
for i in range(len(liste_scaler_name)):
    for j in range(len(liste_classifier_name)):
        print(n)
        n+=1
        acc, fscore = calculus_function(liste_classifier[j], liste_scaler[i])
        
        liste_acc[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = acc
        liste_fscore[liste_scaler_name[i]+" et "+ liste_classifier_name[j]] = fscore

0
Learning rate set to 0.341155
0:	learn: 0.5614122	total: 434ms	remaining: 7m 13s
1:	learn: 0.5126467	total: 885ms	remaining: 7m 21s
2:	learn: 0.4838662	total: 1.24s	remaining: 6m 51s
3:	learn: 0.4659050	total: 1.65s	remaining: 6m 51s
4:	learn: 0.4588397	total: 2.1s	remaining: 6m 58s
5:	learn: 0.4430167	total: 2.54s	remaining: 7m 1s
6:	learn: 0.4356988	total: 2.99s	remaining: 7m 3s
7:	learn: 0.4242636	total: 3.42s	remaining: 7m 3s
8:	learn: 0.4132378	total: 3.9s	remaining: 7m 9s
9:	learn: 0.4071142	total: 4.31s	remaining: 7m 6s
10:	learn: 0.3995535	total: 4.66s	remaining: 6m 58s
11:	learn: 0.3933603	total: 5.03s	remaining: 6m 54s
12:	learn: 0.3894657	total: 5.42s	remaining: 6m 51s
13:	learn: 0.3846137	total: 5.82s	remaining: 6m 49s
14:	learn: 0.3812898	total: 6.23s	remaining: 6m 49s
15:	learn: 0.3724681	total: 6.63s	remaining: 6m 48s
16:	learn: 0.3666814	total: 7.07s	remaining: 6m 48s
17:	learn: 0.3635548	total: 7.45s	remaining: 6m 46s
18:	learn: 0.3602399	total: 7.83s	remaining: 6m 4

158:	learn: 0.1629893	total: 1m 1s	remaining: 5m 22s
159:	learn: 0.1622927	total: 1m 1s	remaining: 5m 22s
160:	learn: 0.1616806	total: 1m 1s	remaining: 5m 21s
161:	learn: 0.1606404	total: 1m 2s	remaining: 5m 21s
162:	learn: 0.1599030	total: 1m 2s	remaining: 5m 21s
163:	learn: 0.1593502	total: 1m 2s	remaining: 5m 20s
164:	learn: 0.1587403	total: 1m 3s	remaining: 5m 20s
165:	learn: 0.1582369	total: 1m 3s	remaining: 5m 19s
166:	learn: 0.1578269	total: 1m 4s	remaining: 5m 19s
167:	learn: 0.1573876	total: 1m 4s	remaining: 5m 19s
168:	learn: 0.1567065	total: 1m 4s	remaining: 5m 18s
169:	learn: 0.1562846	total: 1m 5s	remaining: 5m 18s
170:	learn: 0.1561131	total: 1m 5s	remaining: 5m 17s
171:	learn: 0.1557111	total: 1m 5s	remaining: 5m 17s
172:	learn: 0.1554482	total: 1m 6s	remaining: 5m 16s
173:	learn: 0.1545790	total: 1m 6s	remaining: 5m 16s
174:	learn: 0.1543637	total: 1m 7s	remaining: 5m 15s
175:	learn: 0.1537808	total: 1m 7s	remaining: 5m 15s
176:	learn: 0.1534610	total: 1m 7s	remaining: 

311:	learn: 0.1190682	total: 1m 58s	remaining: 4m 20s
312:	learn: 0.1189600	total: 1m 58s	remaining: 4m 20s
313:	learn: 0.1188430	total: 1m 58s	remaining: 4m 19s
314:	learn: 0.1186607	total: 1m 59s	remaining: 4m 19s
315:	learn: 0.1184342	total: 1m 59s	remaining: 4m 19s
316:	learn: 0.1183233	total: 2m	remaining: 4m 18s
317:	learn: 0.1180845	total: 2m	remaining: 4m 18s
318:	learn: 0.1180110	total: 2m	remaining: 4m 17s
319:	learn: 0.1178208	total: 2m 1s	remaining: 4m 17s
320:	learn: 0.1177286	total: 2m 1s	remaining: 4m 16s
321:	learn: 0.1176333	total: 2m 1s	remaining: 4m 16s
322:	learn: 0.1175158	total: 2m 2s	remaining: 4m 16s
323:	learn: 0.1174639	total: 2m 2s	remaining: 4m 15s
324:	learn: 0.1172790	total: 2m 2s	remaining: 4m 15s
325:	learn: 0.1171021	total: 2m 3s	remaining: 4m 15s
326:	learn: 0.1169199	total: 2m 3s	remaining: 4m 14s
327:	learn: 0.1168407	total: 2m 4s	remaining: 4m 14s
328:	learn: 0.1166984	total: 2m 4s	remaining: 4m 13s
329:	learn: 0.1164765	total: 2m 4s	remaining: 4m 1

464:	learn: 0.0997074	total: 2m 54s	remaining: 3m 20s
465:	learn: 0.0996334	total: 2m 54s	remaining: 3m 20s
466:	learn: 0.0995845	total: 2m 55s	remaining: 3m 19s
467:	learn: 0.0994496	total: 2m 55s	remaining: 3m 19s
468:	learn: 0.0994020	total: 2m 55s	remaining: 3m 19s
469:	learn: 0.0993347	total: 2m 56s	remaining: 3m 18s
470:	learn: 0.0992364	total: 2m 56s	remaining: 3m 18s
471:	learn: 0.0988718	total: 2m 57s	remaining: 3m 18s
472:	learn: 0.0987319	total: 2m 57s	remaining: 3m 17s
473:	learn: 0.0986658	total: 2m 57s	remaining: 3m 17s
474:	learn: 0.0985641	total: 2m 58s	remaining: 3m 16s
475:	learn: 0.0984895	total: 2m 58s	remaining: 3m 16s
476:	learn: 0.0983789	total: 2m 58s	remaining: 3m 16s
477:	learn: 0.0983247	total: 2m 59s	remaining: 3m 15s
478:	learn: 0.0982473	total: 2m 59s	remaining: 3m 15s
479:	learn: 0.0981836	total: 3m	remaining: 3m 15s
480:	learn: 0.0981433	total: 3m	remaining: 3m 14s
481:	learn: 0.0980888	total: 3m	remaining: 3m 14s
482:	learn: 0.0980492	total: 3m 1s	remai

618:	learn: 0.0884889	total: 3m 51s	remaining: 2m 22s
619:	learn: 0.0884278	total: 3m 52s	remaining: 2m 22s
620:	learn: 0.0883796	total: 3m 52s	remaining: 2m 21s
621:	learn: 0.0882597	total: 3m 52s	remaining: 2m 21s
622:	learn: 0.0882006	total: 3m 53s	remaining: 2m 21s
623:	learn: 0.0881457	total: 3m 53s	remaining: 2m 20s
624:	learn: 0.0881037	total: 3m 54s	remaining: 2m 20s
625:	learn: 0.0880636	total: 3m 54s	remaining: 2m 20s
626:	learn: 0.0880104	total: 3m 54s	remaining: 2m 19s
627:	learn: 0.0879710	total: 3m 55s	remaining: 2m 19s
628:	learn: 0.0879416	total: 3m 55s	remaining: 2m 18s
629:	learn: 0.0878953	total: 3m 55s	remaining: 2m 18s
630:	learn: 0.0878815	total: 3m 56s	remaining: 2m 18s
631:	learn: 0.0878443	total: 3m 56s	remaining: 2m 17s
632:	learn: 0.0878028	total: 3m 56s	remaining: 2m 17s
633:	learn: 0.0877727	total: 3m 57s	remaining: 2m 16s
634:	learn: 0.0877267	total: 3m 57s	remaining: 2m 16s
635:	learn: 0.0876631	total: 3m 57s	remaining: 2m 16s
636:	learn: 0.0875858	total:

...

260:	learn: 0.1312684	total: 1m 37s	remaining: 4m 36s
261:	learn: 0.1311099	total: 1m 38s	remaining: 4m 36s
262:	learn: 0.1308793	total: 1m 38s	remaining: 4m 35s
263:	learn: 0.1306824	total: 1m 38s	remaining: 4m 35s
264:	learn: 0.1305480	total: 1m 39s	remaining: 4m 35s
265:	learn: 0.1302630	total: 1m 39s	remaining: 4m 34s
266:	learn: 0.1299422	total: 1m 39s	remaining: 4m 34s
267:	learn: 0.1297394	total: 1m 40s	remaining: 4m 33s
268:	learn: 0.1292173	total: 1m 40s	remaining: 4m 33s
269:	learn: 0.1290330	total: 1m 41s	remaining: 4m 33s
270:	learn: 0.1287290	total: 1m 41s	remaining: 4m 32s
271:	learn: 0.1285267	total: 1m 41s	remaining: 4m 32s
272:	learn: 0.1283742	total: 1m 42s	remaining: 4m 31s
273:	learn: 0.1281240	total: 1m 42s	remaining: 4m 31s
274:	learn: 0.1279557	total: 1m 42s	remaining: 4m 31s
275:	learn: 0.1278251	total: 1m 43s	remaining: 4m 30s
276:	learn: 0.1275862	total: 1m 43s	remaining: 4m 30s
277:	learn: 0.1273899	total: 1m 43s	remaining: 4m 29s
278:	learn: 0.1272465	total:

413:	learn: 0.1057214	total: 2m 34s	remaining: 3m 39s
414:	learn: 0.1056331	total: 2m 35s	remaining: 3m 38s
415:	learn: 0.1054421	total: 2m 35s	remaining: 3m 38s
416:	learn: 0.1053623	total: 2m 36s	remaining: 3m 38s
417:	learn: 0.1052007	total: 2m 36s	remaining: 3m 37s
418:	learn: 0.1051073	total: 2m 36s	remaining: 3m 37s
419:	learn: 0.1050740	total: 2m 37s	remaining: 3m 37s
420:	learn: 0.1048301	total: 2m 37s	remaining: 3m 36s
421:	learn: 0.1047306	total: 2m 37s	remaining: 3m 36s
422:	learn: 0.1045691	total: 2m 38s	remaining: 3m 35s
423:	learn: 0.1042906	total: 2m 38s	remaining: 3m 35s
424:	learn: 0.1041154	total: 2m 39s	remaining: 3m 35s
425:	learn: 0.1040845	total: 2m 39s	remaining: 3m 34s
426:	learn: 0.1039735	total: 2m 39s	remaining: 3m 34s
427:	learn: 0.1039221	total: 2m 40s	remaining: 3m 34s
428:	learn: 0.1037871	total: 2m 40s	remaining: 3m 33s
429:	learn: 0.1036588	total: 2m 40s	remaining: 3m 33s
430:	learn: 0.1035338	total: 2m 41s	remaining: 3m 32s
431:	learn: 0.1034216	total:

566:	learn: 0.0923460	total: 3m 31s	remaining: 2m 41s
567:	learn: 0.0922879	total: 3m 32s	remaining: 2m 41s
568:	learn: 0.0922396	total: 3m 32s	remaining: 2m 41s
569:	learn: 0.0921615	total: 3m 33s	remaining: 2m 40s
570:	learn: 0.0920998	total: 3m 33s	remaining: 2m 40s
571:	learn: 0.0920333	total: 3m 33s	remaining: 2m 39s
572:	learn: 0.0919744	total: 3m 34s	remaining: 2m 39s
573:	learn: 0.0918601	total: 3m 34s	remaining: 2m 39s
574:	learn: 0.0917838	total: 3m 34s	remaining: 2m 38s
575:	learn: 0.0917192	total: 3m 35s	remaining: 2m 38s
576:	learn: 0.0916751	total: 3m 35s	remaining: 2m 38s
577:	learn: 0.0916308	total: 3m 36s	remaining: 2m 37s
578:	learn: 0.0915706	total: 3m 36s	remaining: 2m 37s
579:	learn: 0.0915242	total: 3m 36s	remaining: 2m 36s
580:	learn: 0.0915121	total: 3m 37s	remaining: 2m 36s
581:	learn: 0.0914370	total: 3m 37s	remaining: 2m 36s
582:	learn: 0.0914134	total: 3m 37s	remaining: 2m 35s
583:	learn: 0.0913204	total: 3m 38s	remaining: 2m 35s
584:	learn: 0.0912261	total:

720:	learn: 0.0839857	total: 4m 28s	remaining: 1m 43s
721:	learn: 0.0839318	total: 4m 28s	remaining: 1m 43s
722:	learn: 0.0838541	total: 4m 29s	remaining: 1m 43s
723:	learn: 0.0838179	total: 4m 29s	remaining: 1m 42s
724:	learn: 0.0836725	total: 4m 30s	remaining: 1m 42s
725:	learn: 0.0836488	total: 4m 30s	remaining: 1m 42s
726:	learn: 0.0835656	total: 4m 30s	remaining: 1m 41s
727:	learn: 0.0835211	total: 4m 31s	remaining: 1m 41s
728:	learn: 0.0834961	total: 4m 31s	remaining: 1m 40s
729:	learn: 0.0834217	total: 4m 31s	remaining: 1m 40s
730:	learn: 0.0833947	total: 4m 32s	remaining: 1m 40s
731:	learn: 0.0833598	total: 4m 32s	remaining: 1m 39s
732:	learn: 0.0832428	total: 4m 32s	remaining: 1m 39s
733:	learn: 0.0831668	total: 4m 33s	remaining: 1m 39s
734:	learn: 0.0831273	total: 4m 33s	remaining: 1m 38s
735:	learn: 0.0830961	total: 4m 34s	remaining: 1m 38s
736:	learn: 0.0830723	total: 4m 34s	remaining: 1m 37s
737:	learn: 0.0830116	total: 4m 34s	remaining: 1m 37s
738:	learn: 0.0829732	total:

874:	learn: 0.0779746	total: 5m 25s	remaining: 46.5s
875:	learn: 0.0779391	total: 5m 25s	remaining: 46.1s
876:	learn: 0.0779236	total: 5m 26s	remaining: 45.7s
877:	learn: 0.0779058	total: 5m 26s	remaining: 45.4s
878:	learn: 0.0778792	total: 5m 26s	remaining: 45s
879:	learn: 0.0778733	total: 5m 27s	remaining: 44.6s
880:	learn: 0.0778552	total: 5m 27s	remaining: 44.3s
881:	learn: 0.0778223	total: 5m 28s	remaining: 43.9s
882:	learn: 0.0778121	total: 5m 28s	remaining: 43.5s
883:	learn: 0.0777565	total: 5m 28s	remaining: 43.1s
884:	learn: 0.0777509	total: 5m 29s	remaining: 42.8s
885:	learn: 0.0777424	total: 5m 29s	remaining: 42.4s
886:	learn: 0.0777061	total: 5m 29s	remaining: 42s
887:	learn: 0.0776861	total: 5m 30s	remaining: 41.6s
888:	learn: 0.0775770	total: 5m 30s	remaining: 41.3s
889:	learn: 0.0775423	total: 5m 30s	remaining: 40.9s
890:	learn: 0.0775154	total: 5m 31s	remaining: 40.5s
891:	learn: 0.0774465	total: 5m 31s	remaining: 40.2s
892:	learn: 0.0774104	total: 5m 32s	remaining: 39.

In [16]:
liste_acc

{'MinMaxScaler et VotingClassifier': 0.69662835055126,
 'StandardScaler et VotingClassifier': 0.6591709736004868,
 'QuantileTransformer et VotingClassifier': 0.6939032414115365,
 'RobustScaler et VotingClassifier': 0.6999360874953949,
 'MaxAbsScaler et VotingClassifier': 0.5503949510298388,
 'PowerTransformer et VotingClassifier': 0.7023439881638279}

In [17]:
liste_fscore

{'MinMaxScaler et VotingClassifier': 0.7313243021767953,
 'StandardScaler et VotingClassifier': 0.6877224988290664,
 'QuantileTransformer et VotingClassifier': 0.731310697418948,
 'RobustScaler et VotingClassifier': 0.7229658622114852,
 'MaxAbsScaler et VotingClassifier': 0.6191262265750815,
 'PowerTransformer et VotingClassifier': 0.7481739322219596}